# 루브릭
|평가문항|상세기준|self check|
|:-------|:-------|:-----------------------|
|1. 챗봇 훈련데이터 전처리 과정이 체계적으로 진행되었는가?|챗봇 훈련데이터를 위한 전처리와 augmentation이 적절히 수행되어 3만개 가량의 훈련데이터셋이 구축되었다.|OK|
|2. transformer 모델을 활용한 챗봇 모델이 과적합을 피해 안정적으로 훈련되었는가?|과적합을 피할 수 있는 하이퍼파라미터 셋이 적절히 제시되었다.|OK|
|3. 챗봇이 사용자의 질문에 그럴듯한 형태로 답하는 사례가 있는가?|주어진 예문을 포함하여 챗봇에 던진 질문에 적절히 답하는 사례가 제출되었다.|OK|

### dataset
1. [songys/Chatbot_data](https://github.com/songys/Chatbot_data)
    * 챗봇 트레이닝용 문답 페어 11,823개
    * 일상다반사 0, 이별(부정) 1, 사랑(긍정) 2로 레이블링


### 적용할 알고리즘
1. Mecab 토큰나이저 
2. Transformer
3. 데이터 증강 : 한국어로 Pre-trained Embedding 모델 (Word2Vec) 

### 성능 평가 지표  
1. BLUE(BiLingual Understudy Evaluation)

## 문제 정의  

> Transformer로 Chatbot 만들기

## 라이브러리 버전 확인

In [17]:
from IPython.core.interactiveshell import InteractiveShell
InteractiveShell.ast_node_interactivity = "all"
from IPython.display import Image
#Image(filename='optimizer.png') 

In [2]:
!pip install --upgrade gensim==3.8.3


     |████████████████████████████████| 23.4 MB 6.3 MB/s            
  Preparing metadata (setup.py) ... done
  Created wheel for gensim: filename=gensim-3.8.3-cp39-cp39-linux_x86_64.whl size=24328218 sha256=92bc1801387d086d20bb78fa6315c7dc30e6aa7ba94b5d2a92c0575240338a95
  Stored in directory: /aiffel/.cache/pip/wheels/ca/5d/af/618594ec2f28608c1d6ee7d2b7e95a3e9b06551e3b80a491d6
Successfully built gensim
  Attempting uninstall: gensim
    Found existing installation: gensim 4.1.2
    Uninstalling gensim-4.1.2:
      Successfully uninstalled gensim-4.1.2


In [18]:
import numpy 
import pandas 
import tensorflow 
import nltk
import gensim

print(numpy.__version__)
print(pandas.__version__)
print(tensorflow.__version__)
print(nltk.__version__)
print(gensim.__version__)

import pandas as pd

1.21.4
1.3.3
2.6.0
3.6.5
3.8.3


In [20]:
import numpy as np
import pandas as pd
import tensorflow as tf
import sentencepiece as spm
from nltk.translate.bleu_score import sentence_bleu
from nltk.translate.bleu_score import SmoothingFunction


import re
import os
import random
import math

from tqdm.notebook import tqdm
#from tqdm import tqdm
import matplotlib.pyplot as plt

print(tf.__version__)

2.6.0


## Step 1. 데이터 다운로드

* [songys/Chatbot_data](https://github.com/songys/Chatbot_data)
* questions, answers 변수에 나누어 저장

In [21]:
file_path = './data/ChatbotData.csv'
data = pd.read_csv(file_path)
data
#data['label'].unique()

Q                         A  label
0                       12시 땡!                하루가 또 가네요.      0
1                  1지망 학교 떨어졌어                 위로해 드립니다.      0
2                 3박4일 놀러가고 싶다               여행은 언제나 좋죠.      0
3              3박4일 정도 놀러가고 싶다               여행은 언제나 좋죠.      0
4                      PPL 심하네                눈살이 찌푸려지죠.      0
...                        ...                       ...    ...
11818           훔쳐보는 것도 눈치 보임.        티가 나니까 눈치가 보이는 거죠!      2
11819           훔쳐보는 것도 눈치 보임.             훔쳐보는 거 티나나봐요.      2
11820              흑기사 해주는 짝남.                    설렜겠어요.      2
11821  힘든 연애 좋은 연애라는게 무슨 차이일까?  잘 헤어질 수 있는 사이 여부인 거 같아요.      2
11822               힘들어서 결혼할까봐        도피성 결혼은 하지 않길 바라요.      2

[11823 rows x 3 columns]

In [22]:
# Null 확인
data.info()
data.isnull().sum()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 11823 entries, 0 to 11822
Data columns (total 3 columns):
 #   Column  Non-Null Count  Dtype 
---  ------  --------------  ----- 
 0   Q       11823 non-null  object
 1   A       11823 non-null  object
 2   label   11823 non-null  int64 
dtypes: int64(1), object(2)
memory usage: 277.2+ KB


Q        0
A        0
label    0
dtype: int64

In [23]:
# 중복데이터 확인
data.duplicated().sum()
data['Q'].duplicated().sum()
data['A'].duplicated().sum()

0

161

4044

In [24]:
mask = data.duplicated(subset=['Q']) == True
data[mask]

data[data['Q'] == data.loc[196,'Q']]
data[data['Q'] == data.loc[235,'Q']]
data[data['Q'] == data.loc[1294]['Q']]
data[data['Q'] == data.loc[1445]['Q']]

Q                A  label
196               고양이 키우고 싶어     가족들과 상의해보세요.      0
235                공시 준비 힘들어         잘 될 거예요.      0
1294                 돈 벌고 싶어      많이 벌수록 좋아요.      0
1445               로또 번호 알려줘        알면 제가 하죠.      0
1481                 마음이 울적해       거리를 걸어보세요.      0
...                      ...              ...    ...
11642    착해서 잘해주는 건지 좋아하는 건지     헷갈린다고 말해보세요.      2
11649         첫 눈에 반하는게 가능해?        당연히 가능하죠.      2
11658                첫사랑 생각나   지금의 사랑에 충실하세요.      2
11732  커플여행이 나을까 그냥 우리끼리 갈까?  저는 둘이 가는 게 좋아요.      2
11819         훔쳐보는 것도 눈치 보임.    훔쳐보는 거 티나나봐요.      2

[161 rows x 3 columns]

Q             A  label
195  고양이 키우고 싶어  자신을 먼저 키우세요.      0
196  고양이 키우고 싶어  가족들과 상의해보세요.      0

Q         A  label
234  공시 준비 힘들어  합격 기원해요!      0
235  공시 준비 힘들어  잘 될 거예요.      0

Q            A  label
1293  돈 벌고 싶어         저도요.      0
1294  돈 벌고 싶어  많이 벌수록 좋아요.      0

Q                    A  label
1444  로또 번호 알려줘  제가 알면 제가 먼저 했을 거예요.      0
1445  로또 번호 알려줘            알면 제가 하죠.      0

In [25]:
mask = data.duplicated(subset=['A']) == True
data[mask]

data[data['A'] == data.loc[3,'A']]
data[data['A'] == data.loc[6,'A']]
data[data['A'] == data.loc[12]['A']]
data[data['A'] == data.loc[18]['A']]

Q                                    A  \
3                       3박4일 정도 놀러가고 싶다                          여행은 언제나 좋죠.   
6                               SD카드 안돼                   다시 새로 사는 게 마음 편해요.   
9                     SNS 시간낭비인데 자꾸 보게됨                        시간을 정하고 해보세요.   
12                          가끔 뭐하는지 궁금해                        그 사람도 그럴 거예요.   
18                       가스불 켜놓고 나온거 같아                  빨리 집에 돌아가서 끄고 나오세요.   
...                                 ...                                  ...   
11806         혼자만 설레고 혼자서 끝내는 짝사랑 그만할래.                            맘고생 많았어요.   
11807                     화이트데이에 고백할까요?            선물을 주면서 솔직하고 당당하게 고백해보세요.   
11809  확실히 날 좋아하는 걸 아는 남자랑 친구가 될 수 있을까?                  그 사람을 위해서는 그러면 안돼요.   
11816                 회식하는데 나만 챙겨줘. 썸임?  호감이 있을 수도 있어요. 그렇지만 조금 더 상황을 지켜보세요.   
11822                        힘들어서 결혼할까봐                   도피성 결혼은 하지 않길 바라요.   

       label  
3          0  
6          0  
9          0  
12         0  
18         0  
...      ...  
11806      2  
11807      2  
11809      2  
11816      2  
11822      2  

[4044 rows x 3 columns]

Q            A  label
2     3박4일 놀러가고 싶다  여행은 언제나 좋죠.      0
3  3박4일 정도 놀러가고 싶다  여행은 언제나 좋죠.      0

Q                   A  label
5  SD카드 망가졌어  다시 새로 사는 게 마음 편해요.      0
6    SD카드 안돼  다시 새로 사는 게 마음 편해요.      0

Q              A  label
11       가끔 궁금해  그 사람도 그럴 거예요.      0
12  가끔 뭐하는지 궁금해  그 사람도 그럴 거예요.      0

Q                    A  label
17      가스불 켜고 나갔어  빨리 집에 돌아가서 끄고 나오세요.      0
18  가스불 켜놓고 나온거 같아  빨리 집에 돌아가서 끄고 나오세요.      0

#### 중복 데이터 제거 시

In [9]:
# 중복 데이터 제거
data.drop_duplicates(subset=['Q'],inplace=True)
data.drop_duplicates(subset=['A'],inplace=True)
data.shape

# 중복데이터 제거 확인
data.duplicated().sum()
data['Q'].duplicated().sum()
data['A'].duplicated().sum()

(7731, 3)

0

0

0

In [10]:
questions = [sen for sen in data['Q']]
answers = [sen for sen in data['A']]
len(questions)
len(answers)

7731

7731

#### 중복 데이터 미제거 시

In [26]:
questions = [sen for sen in data['Q']]
answers = [sen for sen in data['A']]
len(questions)
len(answers)

11823

11823

## Step 2. 데이터 정제

* preprocess_sentence() 함수
1. 영문자의 경우, 모두 소문자로 변환
2. 영문자와 한글, 숫자, 그리고 주요 특수문자를 제외하곤 정규식을 활용하여 모두 제거


* 문장부호 양옆에 공백을 추가하는 등 이전과 다르게 생략된 기능들은 우리가 사용할 토크나이저가 지원하기 때문에 굳이 구현하지 않아도 됨

In [27]:
import re
# 전처리 함수
def preprocess_sentence(sentence):
    sentence = sentence.lower().strip()

    # 단어와 구두점(punctuation) 사이의 거리를 만듭니다.
    # 예를 들어서 "I am a student." => "I am a student ."와 같이
    # student와 온점 사이에 거리를 만듭니다.
    #sentence = re.sub(r"([?.!,])", r" \1 ", sentence)
    sentence = re.sub(r'[" "]+', " ", sentence)

    # (a-z, A-Z, ".", "?", "!", ",")를 제외한 모든 문자를 공백인 ' '로 대체합니다.
    sentence = re.sub(r"[^a-zA-Z?.!가-힣ㄱ-ㅎㅏ-ㅣ0-9]+", " ", sentence)
    sentence = sentence.strip()
    return sentence

preprocess_sentence("02 3    zzz S  ㅇ ㄴ ㅎ ㄷ 오늘 ???~!,")

'02 3 zzz s ㅇ ㄴ ㅎ ㄷ 오늘 ??? !'

## Step 3. 데이터 토큰화

* KoNLPy의 mecab 클래스를 사용

* build_corpus() 함수 구현
1. 소스 문장 데이터와 타겟 문장 데이터를 입력으로 받습니다.
2. 데이터를 앞서 정의한 preprocess_sentence() 함수로 정제하고, 토큰화합니다.
3. 토큰화는 전달받은 토크나이즈 함수를 사용합니다. 이번엔 mecab.morphs 함수를 전달하시면 됩니다.
4. 토큰의 개수가 일정 길이 이상인 문장은 데이터에서 제외합니다.
5. 중복되는 문장은 데이터에서 제외합니다. 소스 : 타겟 쌍을 비교하지 않고 소스는 소스대로 타겟은 타겟대로 검사합니다. 중복 쌍이 흐트러지지 않도록 유의!

* 토큰화하기  
questions -> que_corpus  
answers -> ans_corpus  

In [28]:
from konlpy.tag import Mecab

tokenizer = Mecab()
sequence_len = 39

def build_corpus(src_sen, tgt_sen):
    
    src_corpus = []
    tgt_corpus = []

    assert len(src_sen) == len(tgt_sen)
        
    for index in range(len(src_sen)):
        src_temp = preprocess_sentence(src_sen[index])
        tgt_temp = preprocess_sentence(tgt_sen[index])

        src_temp = tokenizer.morphs(src_temp) #토근화
        tgt_temp = tokenizer.morphs(tgt_temp) #토큰화
        
        if (len(src_temp) <= sequence_len) & (len(tgt_temp) <= sequence_len):
            src_corpus.append(src_temp)
            tgt_corpus.append(tgt_temp)
        else:
            print(len(src_temp),len(tgt_temp))

    return src_corpus,tgt_corpus


In [29]:
que_corpus, ans_corpus = build_corpus(questions, answers)

print('전체 샘플 수 :', len(que_corpus))
print('전체 샘플 수 :', len(ans_corpus))
list(zip(que_corpus[:5], ans_corpus[:5]))


전체 샘플 수 : 11823
전체 샘플 수 : 11823


[(['12', '시', '땡', '!'], ['하루', '가', '또', '가', '네요', '.']),
 (['1', '지망', '학교', '떨어졌', '어'], ['위로', '해', '드립니다', '.']),
 (['3', '박', '4', '일', '놀', '러', '가', '고', '싶', '다'],
  ['여행', '은', '언제나', '좋', '죠', '.']),
 (['3', '박', '4', '일', '정도', '놀', '러', '가', '고', '싶', '다'],
  ['여행', '은', '언제나', '좋', '죠', '.']),
 (['ppl', '심하', '네'], ['눈살', '이', '찌푸려', '지', '죠', '.'])]

## Step 4. Augmentation

한국어로 사전 훈련된 Embedding 모델(Word2vec)을 다운로드
* [Kyubyong/wordvectors](https://github.com/Kyubyong/wordvectors)

In [30]:
from gensim.models.word2vec import Word2Vec

file_path = './data/ko.bin'
wv_model = Word2Vec.load(file_path)
a = wv_model.wv.most_similar("재미")
print(a)

wv_model.wv.most_similar('재미')[0][0]

[('취미', 0.5857348442077637), ('유머', 0.5140613913536072), ('매력', 0.5105490684509277), ('흥미', 0.4988338351249695), ('공짜', 0.4960595667362213), ('일자리', 0.49294644594192505), ('즐거움', 0.48700767755508423), ('비애', 0.4836210310459137), ('관객', 0.48286449909210205), ('향수', 0.4823310971260071)]


'취미'

In [31]:
def lexical_sub(sentence, word2vec):
    res = ""
    #toks = sentence.split()
    toks = sentence

    try:
        _from = random.choice(toks)
        _to = word2vec.wv.most_similar(_from)[0][0]
        #print("_from_:", _from, "_to:",_to)
        
    except:   # 단어장에 없는 단어
        return None

    for tok in toks:
        if tok is _from: res += _to + " "
        else: res += tok + " "

    return res

In [15]:
#test 
new_corpus = []

for old_src in tqdm(que_corpus):
    new_src = lexical_sub(old_src, wv_model)
    print("old: ",old_src, "new: ",new_src)
    if new_src is not None: 
        new_corpus.append(new_src.split())
    # Augmentation이 없더라도 원본 문장을 포함시킵니다
    new_corpus.append(old_src)

#print(new_corpus[:10])
len(new_corpus)

  0%|          | 0/7731 [00:00<?, ?it/s]

old:  ['12', '시', '땡', '!'] new:  None
old:  ['1', '지망', '학교', '떨어졌', '어'] new:  None
old:  ['3', '박', '4', '일', '놀', '러', '가', '고', '싶', '다'] new:  3 박 4 일 살 러 가 고 싶 다 
old:  ['ppl', '심하', '네'] new:  ppl 강하 네 
old:  ['sd', '카드', '망가졌', '어'] new:  None
old:  ['sns', '맞', '팔', '왜', '안', '하', '지', 'ㅠㅠ'] new:  None
old:  ['sns', '시간', '낭비', '인', '거', '아', '는데', '매일', '하', '는', '중'] new:  sns 분간 낭비 인 거 아 는데 매일 하 는 중 
old:  ['sns', '보', '면', '나', '만', '빼', '고', '다', '행복', '해', '보여'] new:  sns 살펴보 면 나 만 빼 고 다 행복 해 보여 
old:  ['가끔', '궁금', '해'] new:  가끔 궁금 해의 
old:  ['가끔', '은', '혼자', '인', '게', '좋', '다'] new:  가끔 은 혼자 인은 게 좋 다 
old:  ['가난', '한', '자', '의', '설움'] new:  가난 한두 자 의 설움 
old:  ['가만', '있', '어도', '땀', '난다'] new:  가만 없 어도 땀 난다 
old:  ['가상', '화폐', '쫄딱', '망함'] new:  가상현실 화폐 쫄딱 망함 
old:  ['가스', '불', '켜', '고', '나갔', '어'] new:  가스 불 켜지 고 나갔 어 
old:  ['가스', '비', '너무', '많이', '나왔', '다', '.'] new:  증기 비 너무 많이 나왔 다 . 
old:  ['가스', '비', '비싼데', '감기', '걸리', '겠', '어'] new:  None
old:  ['가장', '확실', '한',

old:  ['궁금', '하', '면', '오', '백', '원'] new:  궁금 하 면 오 백 원의 
old:  ['궁금', '해'] new:  궁금하 해 
old:  ['귀', '아파'] new:  None
old:  ['귀', '가', '가려워'] new:  None
old:  ['귀농', '어때', '?'] new:  None
old:  ['그', '사람', '이', '나', '안', '좋아하', '는', '거', '같', '아'] new:  그 젊은이 이 나 안 좋아하 는 거 같 아 
old:  ['그', '사람', '이', '나', '좋', '아', '해', '줬', '으면', '좋', '겠', '다'] new:  그 사람 이 나 좋 아 해 줬 다면 좋 겠 다 
old:  ['그', '사람', '이', '행복', '했으면', '좋', '겠', '다'] new:  그 사람 그러 행복 했으면 좋 겠 다 
old:  ['그', '시절', '엔', '다', '그랬', '지'] new:  그 시절 엔 으며 그랬 지 
old:  ['그냥', '내버려', '둬', '주', '었', '으면'] new:  굳이 내버려 둬 주 었 으면 
old:  ['그냥', '선', '볼까', '?'] new:  굳이 선 볼까 ? 
old:  ['그냥', '쉬', '고', '싶', '다'] new:  그냥 쉬 기에 싶 다 
old:  ['그냥', '씹', '어야', '겠다', '.'] new:  그냥 썩 어야 겠다 . 
old:  ['그냥', '이렇게', '살', '고', '싶', '어'] new:  그냥 이렇게 살아오 고 싶 어 
old:  ['그냥', '자', '는', '거', '아니', '지', '?'] new:  그냥 자 는 거 아니 꼼짝 ? 
old:  ['그냥', '택시', '타', '야지', '.'] new:  굳이 택시 타 야지 . 
old:  ['그냥', '할까', '?'] new:  그냥 할까 ... 
old:  ['그냥', '혼자', '밥', '이나', '먹'

old:  ['나', '새', '옷', '샀', '다'] new:  나 감미 옷 샀 다 
old:  ['나', '속', '은', '거', '같', '아'] new:  나 속 은 거 같 아서 
old:  ['나', '속', '은', '듯'] new:  나 속 은데 듯 
old:  ['나', '수학여행', '간다'] new:  None
old:  ['나', '스마트폰', '중독', '인가', '봐'] new:  나 스마트폰 중독 허가 봐 
old:  ['나', '승진', '했', '어'] new:  나의 승진 했 어 
old:  ['나', '실수', '한', '건가'] new:  나 실수 한두 건가 
old:  ['나', '아재', '인가'] new:  나의 아재 인가 
old:  ['나', '아직', '어른', '아닌', '거', '같', '아'] new:  나 아직 어린아이 아닌 거 같 아 
old:  ['나', '열심히', '할', '거', '야'] new:  나 열심히 할 거 야가 
old:  ['나', '오늘', '개불', '쌍'] new:  나 오늘 개불 겹 
old:  ['나', '오늘', '따라', '잘', '생겨', '보이', '네'] new:  None
old:  ['나', '오늘', '상', '받', '았', '지롱'] new:  나 오늘 상 넘겨받 았 지롱 
old:  ['나', '완전', '계', '탔', '어', '!'] new:  나 완벽 계 탔 어 ! 
old:  ['나', '왕따', '야'] new:  나 왕따 야가 
old:  ['나', '왕따', '인', '거', '같', '아'] new:  나 퇴학 인 거 같 아 
old:  ['나', '왜', '멍청', '해'] new:  나 왜 멍청 해의 
old:  ['나', '왜', '이러', '지', '?'] new:  나 과연 이러 지 ? 
old:  ['나', '요즘', '정신', '놓', '고', '살', '고', '있', '는', '거', '같', '아'] new:  나 요즘 정

old:  ['남', '의', '일', '도와', '줘야', '할까'] new:  남 인의 일 도와 줘야 할까 
old:  ['남', '의', '차', '긁', '었', '어', '내', '돈'] new:  남의 의 차 긁 었 어 내 돈 
old:  ['남', '이', '걷', '지', '않', '는', '길', '을', '가', '려고', '해'] new:  남 이 걸어가 지 않 는 길 을 가 려고 해 
old:  ['남자', '보통', '어디', '서', '만나'] new:  남자 대개 어디 서 만나 
old:  ['남자', '친구', '가', '바래다', '줬', '어'] new:  여자 친구 가 바래다 줬 어 
old:  ['남자', '화장', '하', '는', '거', '어때'] new:  남자 화장 하 ㄴ다는 거 어때 
old:  ['남자', '면', '편할', '것', '같', '아'] new:  남자 면 편할 방법 같 아 
old:  ['남자', '인지', '여자', '인지', '알려줘'] new:  남자 인지 여자 판별 알려줘 
old:  ['남자', '친구', '교회', '데려가', '고', '싶', '어'] new:  남자 친구 개신교 데려가 고 싶 어 
old:  ['남자', '친구', '또', '운동', '갔', '어'] new:  None
old:  ['남자', '친구', '생일', '인데', '뭘', '줄까'] new:  여자 친구 생일 인데 뭘 줄까 
old:  ['남자', '친구', '승진', '선물', '로', '뭐', '가', '좋', '을까', '?'] new:  남자 친구 승진 선물 로 뭐 놀드 좋 을까 ? 
old:  ['남자', '친구', '오늘', '따라', '훈훈', '해', '보인다'] new:  남자 연인 오늘 따라 훈훈 해 보인다 
old:  ['남자', '친구', '오늘', '좀', '질린다', '.'] new:  남자 친구 오늘 좀 질린다 는데 
old:  ['남자', '친구', '가', '나', '안', 

...

old:  ['짝', '남', '일', '년', '째', '멀리서', '지켜보', '기', '만', '하', '는', '중', '.'] new:  짝 남 일 년 째 멀리서 지켜보 기 만 시키 는 중 . 
old:  ['짝', '남', '있', '는데', '소개', '들어오', '면', '받', '나요', '?'] new:  짝 남 있 는데 소개 넘어오 면 받 나요 ? 
old:  ['짝', '남', '잊', '으려고', '나', '혼자', '나쁘', '게', '생각', '하', '는', '내', '자신', '이', '증오', '스러워', '.'] new:  짝 남 잊 으려고 나 혼자 좋 게 생각 하 는 내 자신 이 증오 스러워 . 
old:  ['짝', '남', '잊', '으려고', '하', '는데', '인', '스타', '에서', '자꾸', '보여요', '.'] new:  짝 남 잊 으려고 하 는데 인 스타 에서 자꾸 보여요 는데 
old:  ['짝', '남', '전여', '친', '못', '잊', '는', '거', '보', '는', '게', '너무', '맘', '이', '아파', '.'] new:  짝 남의 전여 친 못 잊 는 거 보 는 게 너무 맘 이 아파 . 
old:  ['짝', '남', '정리', '잘', '하', '고', '있', '었', '는데', '자꾸', '꿈', '에', '나와', '.'] new:  짝 남 정리 잘 시키 고 있 었 는데 자꾸 꿈 에 나와 . 
old:  ['짝', '남', '줄', '건데', '센스', '있', '는', '선물', '추천', '해', '주', '세요', '.'] new:  짝 남의 줄 건데 센스 있 는 선물 추천 해 주 세요 . 
old:  ['짝', '남', '표정', '안', '좋', '아서', '괜히', '신경', '쓰여', '.'] new:  쌍 남 표정 안 좋 아서 괜히 신경 쓰여 . 
old:  ['짝', '남', '프', '사랑', '비슷', '한', '거', '하', '고', '싶', '은데'

old:  ['짝', '남', '한테', '시덥', '지', '않', '은', '걸로', '선', '톡', '해도', '될까', '?'] new:  쌍 남 한테 시덥 지 않 은 걸로 선 톡 해도 될까 ? 
old:  ['짝', '남', '한테', '실망', '했', '어요', '.'] new:  짝 남의 한테 실망 했 어요 . 
old:  ['짝', '남', '한테', '아침', '에', '데이트', '신청', '했', '는데', '오늘', '야근', '이', '야', '.'] new:  짝 남 한테 아침 에 코너 신청 했 는데 오늘 야근 이 야 . 
old:  ['짝', '남', '한테', '여러', '번', '차이', '다가', '나중', '에', '사귀', '게', '된', '사람', '도', '있', '을까', '?'] new:  짝 남 한테 여러 번 변화 다가 나중 에 사귀 게 된 사람 도 있 을까 ? 
old:  ['짝', '남', '한테', '은근슬쩍', '좋아하', '는', '티', '내', '는', '방법', '좀', '.'] new:  짝 남 한테 은근슬쩍 싫어하 는 티 내 는 방법 좀 . 
old:  ['짝', '남', '한테', '좋', '아', '하', '는', '거', '들켰', '는데', '그냥', '예전', '처럼', '편하', '게', '지내', '고', '싶', '어', '.'] new:  짝 남 한테 좋 아 하 는 거 들켰 는데 그냥 예전 처럼 편하 게 역임 고 싶 어 . 
old:  ['짝', '남', '한테', '주말', '에', '만나', '자고', '했', '는데', '일', '있', '대', '계속', '언제', '되', '는지', '물어봐도', '되', '나', '.'] new:  짝 남 한테 주말 에 만나 자고 했 는데 일 있 회 계속 언제 되 는지 물어봐도 되 나 . 
old:  ['짝', '남', '한테', '크리스마스', '선물', '할', '건데', '추천', '좀', '.'] new:  짝 남 한테 크리스

old:  ['짝사랑', '하', '는', '남자', '때문', '에', '하루', '에', '도', '몇', '번', '기분', '이', '달라져', '.'] new:  짝사랑 하 는 남자 때문 에 하루 에 도 몇 번 기분 그러 달라져 . 
old:  ['짝사랑', '하', '는', '남자', '가', '외국인', '인데', '어떻게', '다가갈', '수', '있', '을까', '?'] new:  짝사랑 하 는 남자 가 외국인 인데 어떻게 다가갈 가능성 있 을까 ? 
old:  ['짝사랑', '하', '는', '남자', '애', '가', '이사', '간대', '.'] new:  None
old:  ['짝사랑', '하', '는', '사람', '보다', '좋', '은', '사람', '만날', '거', '야', '.'] new:  짝사랑 하 ㄴ다는 사람 보다 좋 은 사람 만날 거 야 . 
old:  ['짝사랑', '하', '는', '사람', '을', '보냈', '습니다', '.', '위로', '해', '주', '세요', '.'] new:  짝사랑 하 는 젊은이 을 보냈 습니다 . 위로 해 주 세요 . 
old:  ['짝사랑', '하', '는', '사람', '이', '날', '좋아할', '확률', '은', '?'] new:  짝사랑 하 는 사람 이 날 좋아할 확률 은 ... 
old:  ['짝사랑', '하', '는', '사람', '이', '날', '좋아할', '리', '는', '없', '겠', '지', '?'] new:  짝사랑 시키 는 사람 이 날 좋아할 리 는 없 겠 지 ? 
old:  ['짝사랑', '하', '는', '사람', '이', '너무', '잘나', '서', '내', '가', '작', '아', '보여', '.'] new:  짝사랑 하 는 사람 이 너무 잘나 서 내 가 작 아서 보여 . 
old:  ['짝사랑', '하', '는', '사람', '이랑', '잘', '됐', '으면', '좋', '겠', '다', '.'] new:  그리워하 하 는 사람 이랑 잘

old:  ['콩깍지', '언제', '벗겨져', '?'] new:  콩깍지 어디 벗겨져 ? 
old:  ['콩깍지', '왜', '안', '벗겨지', '지', '?'] new:  콩깍지 왜 못가 벗겨지 지 ? 
old:  ['콩깍지', '가', '씌', '었', '나', '봐', '.', '아직', '도', '좋', '아', '해', '.'] new:  콩깍지 가 씌 었 나 봐 . 아직 도 좋 아서 해 . 
old:  ['크리스마스', '인데', '만나', '자고', '해도', '됨', '?'] new:  None
old:  ['큰', '시험', '앞두', '고', '짝사랑', '하', '는', '사랑', '이', '생겼', '어요', '.'] new:  큰 시험 앞두 고 짝사랑 하 는 사랑 이 생겼 어요 는데 
old:  ['클럽', '좋', '아', '하', '는', '남자', '는', '좋', '아', '하', '면', '안', '되', '겠', '지', '.'] new:  클럽 좋 아 하 는 여자 는 좋 아 하 면 안 되 겠 지 . 
old:  ['클럽', '에서', '만나', '서', '사귀', '는', '거', '어떻', '게', '생각', '해', '?'] new:  클럽 에서 만나 서 사귀 는 거 어떻 도록 생각 해 ? 
old:  ['클럽', '에서', '만난', '남자', '친구', '와', '오래', '갈', '수', '있', '을까', '?'] new:  아약스 에서 만난 남자 친구 와 오래 갈 수 있 을까 ? 
old:  ['키', '작', '은', '남자', '좋', '아', '하', '는', '여자', '있', '나요', '?'] new:  키 작 은 여자 좋 아 하 는 여자 있 나요 ? 
old:  ['키', '작', '은', '여자', '좋', '아', '하', '는', '남자', '있', '나요', '?'] new:  카 작 은 여자 좋 아 하 는 남자 있 나요 ? 
old:  ['키', '큰', '여자', '는', '별로', '

14310

#### que_corpus,  ans_corpus  따로 따로 증강해 보기

In [28]:
aug_que_corpus = []
aug_ans_corpus = []

In [40]:
#que_corpus 만 증강
#aug_que_corpus = []
#aug_ans_corpus = []

for index in tqdm(range(len(que_corpus))):
    new_src = lexical_sub(que_corpus[index], wv_model)
    print("old:", que_corpus[index], "new: ",new_src)
    if new_src is not None: 
        aug_que_corpus.append(new_src.split())
        aug_ans_corpus.append(ans_corpus[index])
    # Augmentation이 없더라도 원본 문장을 포함시킵니다
    aug_que_corpus.append(que_corpus[index])
    aug_ans_corpus.append(ans_corpus[index])

#print(new_corpus[:10])
len(aug_que_corpus)
len(aug_ans_corpus)

  0%|          | 0/7731 [00:00<?, ?it/s]

old: ['12', '시', '땡', '!'] new:  12 시가 땡 ! 
old: ['1', '지망', '학교', '떨어졌', '어'] new:  None
old: ['3', '박', '4', '일', '놀', '러', '가', '고', '싶', '다'] new:  3 박 4 일 놀 러 가 고 싶 으며 
old: ['ppl', '심하', '네'] new:  ppl 강하 네 
old: ['sd', '카드', '망가졌', '어'] new:  sd 단말기 망가졌 어 
old: ['sns', '맞', '팔', '왜', '안', '하', '지', 'ㅠㅠ'] new:  sns 맞 팔 과연 안 하 지 ㅠㅠ 
old: ['sns', '시간', '낭비', '인', '거', '아', '는데', '매일', '하', '는', '중'] new:  sns 시간 낭비 인 거 아 으며 매일 하 는 중 
old: ['sns', '보', '면', '나', '만', '빼', '고', '다', '행복', '해', '보여'] new:  sns 살펴보 면 나 만 빼 고 다 행복 해 보여 
old: ['가끔', '궁금', '해'] new:  가끔 궁금 해의 
old: ['가끔', '은', '혼자', '인', '게', '좋', '다'] new:  이따금 은 혼자 인 게 좋 다 
old: ['가난', '한', '자', '의', '설움'] new:  None
old: ['가만', '있', '어도', '땀', '난다'] new:  None
old: ['가상', '화폐', '쫄딱', '망함'] new:  가상현실 화폐 쫄딱 망함 
old: ['가스', '불', '켜', '고', '나갔', '어'] new:  증기 불 켜 고 나갔 어 
old: ['가스', '비', '너무', '많이', '나왔', '다', '.'] new:  증기 비 너무 많이 나왔 다 . 
old: ['가스', '비', '비싼데', '감기', '걸리', '겠', '어'] new:  가스 비 비싼데 감기 매달리 겠 어 
old: ['가장'

old: ['귀', '가', '가려워'] new:  절구 가 가려워 
old: ['귀농', '어때', '?'] new:  None
old: ['그', '사람', '이', '나', '안', '좋아하', '는', '거', '같', '아'] new:  그 사람 이 나 안 싫어하 는 거 같 아 
old: ['그', '사람', '이', '나', '좋', '아', '해', '줬', '으면', '좋', '겠', '다'] new:  그 사람 이 나 좋 아 해 줬 으면 좋 겠 으며 
old: ['그', '사람', '이', '행복', '했으면', '좋', '겠', '다'] new:  그녀 사람 이 행복 했으면 좋 겠 다 
old: ['그', '시절', '엔', '다', '그랬', '지'] new:  그 시절 랴쿠 다 그랬 지 
old: ['그냥', '내버려', '둬', '주', '었', '으면'] new:  굳이 내버려 둬 주 었 으면 
old: ['그냥', '선', '볼까', '?'] new:  그냥 선 볼까 ... 
old: ['그냥', '쉬', '고', '싶', '다'] new:  그냥 쉬 기에 싶 다 
old: ['그냥', '씹', '어야', '겠다', '.'] new:  그냥 썩 어야 겠다 . 
old: ['그냥', '이렇게', '살', '고', '싶', '어'] new:  그냥 이렇게 살 고 싶 어서 
old: ['그냥', '자', '는', '거', '아니', '지', '?'] new:  굳이 자 는 거 아니 지 ? 
old: ['그냥', '택시', '타', '야지', '.'] new:  굳이 택시 타 야지 . 
old: ['그냥', '할까', '?'] new:  None
old: ['그냥', '혼자', '밥', '이나', '먹', '어야지'] new:  그냥 혼자 밥 이나 씹 어야지 
old: ['그냥', '혼자', '있', '는', '게', '좋', '아'] new:  그냥 거기 있 는 게 좋 아 
old: ['그', '동안', '잘', '지냈', '나요', '?

old: ['나', '폰', '중독', '인', '거', '같', '애'] new:  나의 폰 중독 인 거 같 애 
old: ['나', '폰', '겜', '너무', '많이', '해'] new:  나 트라흐트 겜 너무 많이 해 
old: ['나', '할', '수', '있', '어'] new:  나 할 수 있 어서 
old: ['나', '함부로', '말', '하', '는', '거', '고치', '고', '싶', '어'] new:  나 함부로 말 하 ㄴ다는 거 고치 고 싶 어 
old: ['나', '혼자', '야근', '해'] new:  나 혼자 야근 해의 
old: ['나', '혼자', '여행', '왔', '는데', '괜찮', '네'] new:  나 혼자 여행 왔 으며 괜찮 네 
old: ['나', '혼자', '서', '축구', '본다'] new:  None
old: ['나', '화장', '을', '너무', '못', '해'] new:  나 치장 을 너무 못 해 
old: ['나', '회사', '에서', '인정받', '고', '싶', '어'] new:  나 회사 에서 인정받 고 겠 어 
old: ['나가', '기', '도', '귀찮', '아'] new:  나아가 기 도 귀찮 아 
old: ['나', '는', '그냥저냥', '사', '는', '거', '같', '아'] new:  None
old: ['나', '는', '모자란', '사람', '인', '거', '같', '아'] new:  나 는 모자란 사람 인 것 같 아 
old: ['나', '는', '뭘', '잘', '할까'] new:  None
old: ['나', '는', '왜', '이렇게', '태어났', '을까', '?'] new:  나 는 왜 이렇게 태어났 을까 ... 
old: ['나', '는', '왜', '태어났을까'] new:  나 ㄴ다는 왜 태어났을까 
old: ['나', '는', '잘', '할', '줄', '아', '는', '게', '없', '는', '것', '같', '아'] new:  나 는 잘 할 줄 

old: ['내', '능력', '이', '너무', '모자라'] new:  내 능력 그러 너무 모자라 
old: ['내', '마음', '을', '알', '아', '줬', '으면'] new:  내 괴로움 을 알 아 줬 으면 
old: ['내', '몸', '이', '여러', '개', '였으면', '좋', '겠', '다'] new:  내 몸 이 몇 개 였으면 좋 겠 다 
old: ['내', '문제', '는', '뭘까'] new:  내 문제점 는 뭘까 
old: ['내', '배우자', '는', '어디', '있', '을까'] new:  내 배우자 ㄴ다는 어디 있 을까 
old: ['내', '사수', '너무', '깐깐', '해'] new:  내 낙수 너무 깐깐 해 
old: ['내', '생각', '이랑', '다른', '사람', '생각', '이', '진짜', '다르', '다는', '걸', '느껴'] new:  내 생각 이랑 다른 젊은이 생각 이 진짜 다르 다는 걸 느껴 
old: ['내', '스타일', '아니', '던데'] new:  내 창법 아니 던데 
old: ['내', '얼굴', '이', '읽히', '나'] new:  내고 얼굴 이 읽히 나 
old: ['내', '외모', '맘', '에', '안', '들', '어'] new:  내고 외모 맘 에 안 들 어 
old: ['내', '월급', '만', '안', '올라'] new:  내 급료 만 안 올라 
old: ['내', '의견', '좀', '존중', '해', '줬', '으면'] new:  내 의견 조금 존중 해 줬 으면 
old: ['내', '의지', '는', '상관없', '나', '봐'] new:  None
old: ['내', '인생', '답', '없', '어'] new:  내 삶 답 없 어 
old: ['내', '인생', '은', '가시밭길', '같', '아'] new:  내 인생 은데 가시밭길 같 아 
old: ['내', '인생', '의', '주인공', '은', '나야'] new:  내 인생 인의 주인공 은 나야 


...

old: ['짝', '남', '이', '고시', '생', '이', '면', '기다려야', '하', '나요', '?'] new:  짝 남 이 고시 생 그러 면 기다려야 하 나요 ? 
old: ['짝', '남', '이', '공무원', '준비', '를', '한다는', '데', '고백', '하', '면', '방해', '가', '될까', '?'] new:  짝 남 이 공무원 준비 를 한다는 데 고백 하 면 방해 가 될까 ... 
old: ['짝', '남', '이', '나', '를', '떠보', '는', '걸까', '?'] new:  짝 남 그러 나 를 떠보 는 걸까 ? 
old: ['짝', '남', '이', '나', '를', '좋아하', '는', '애', '의', '친구', '인데', '어떡', '해', '?'] new:  짝 남 이 나 를 싫어하 는 애 의 친구 인데 어떡 해 ? 
old: ['짝', '남', '이', '나', '한테', '관심', '없', '어', '보여도', '계속', '연락', '하', '고', '들이', '대', '?'] new:  짝 남 그러 나 한테 관심 없 어 보여도 계속 연락 하 고 들이 대 ? 
old: ['짝', '남', '이', '나', '한테', '먼저', '연락', '왔', '으면', '좋', '겠', '어', '.'] new:  짝 남 이 나 한테 먼저 연락 왔 다면 좋 겠 어 . 
old: ['짝', '남', '이', '나', '한테', '여', '지', '준', '것', '같', '아', '.'] new:  짝 남 이 나 한테 여 지 우승자 것 같 아 . 
old: ['짝', '남', '이', '날', '너무', '편하', '게', '생각', '해', '.'] new:  쌍 남 이 날 너무 편하 게 생각 해 . 
old: ['짝', '남', '이', '날', '신경', '쓰', '는', '것', '같', '은', '건', '내', '착각', '일까', '.'] new:  짝 남 이 날 신경 쓰 는 방법 같 은 건 내 착각 

old: ['짝', '녀', '를', '반', '애', '들', '다', '알', '게', '공개', '적', '으로', '좋', '아', '하', '면', '싫', '어', '할까요', '?'] new:  쌍 녀 를 반 애 들 다 알 게 공개 적 으로 좋 아 하 면 싫 어 할까요 ? 
old: ['짝', '녀', '에게', '다가가', '려면', '짝', '녀', '의', '친구', '에게', '먼저', '다가가', '는', '게', '나', '을까', '?'] new:  짝 녀 에게 다가가 려면 짝 녀 의 친구 에게 빨리 다가가 는 게 나 을까 ? 
old: ['짝', '녀', '와', '같이', '드라이브', '갈', '껀', '데', '어디', '로', '갈까', '?'] new:  짝 녀 와 같이 드라이브 갈 껀 데 언제 로 갈까 ? 
old: ['짝', '녀', '의', '전', '남친', '이', '나', '탔', '났', '음', '.'] new:  짝 년 의 전 남친 이 나 탔 났 음 . 
old: ['짝', '녀', '한테', '고백', '했', '는데', '미안', '하', '대', '.'] new:  짝 녀 한테 고백 했 는데 미안 시키 대 . 
old: ['짝', '녀', '한테', '고백', '했', '는데', '잘', '됐', '으면', '.'] new:  짝 녀 한테 고백 했 는데 많이 됐 으면 . 
old: ['짝', '녀', '한테', '공부', '가르쳐', '달', '라고', '해', '볼까'] new:  None
old: ['짝', '녀', '한테', '라인', '왔', '는데', '뭐', '라고', '답장', '해야', '할지', '모르', '겠', '어', '.'] new:  짝 녀 한테 라인 왔 는데 뭐 이라고 답장 해야 할지 모르 겠 어 . 
old: ['짝', '녀', '한테', '문자', '왔', '어', '.'] new:  짝 녀 한테 문자 왔 어 는데 
old: ['짝', '녀', '한테', '여러', '번',

old: ['친구', '의', '구', '남친', '을', '좋아하', '게', '됐', '어요', '.'] new:  친구 의 구 남친 을 좋아하 게 됐 어요 는데 
old: ['친구', '의', '남자', '친구', '가', '눈', '에', '들어와'] new:  친구 의 남자 친구 놀드 눈 에 들어와 
old: ['친구', '의', '남친', '좋', '아', '하', '게', '된', '거', '같', '아'] new:  친구 의 남친 좋 아 하 게 된 거 같 아서 
old: ['친구', '의', '전', '여자', '친구', '가', '좋', '은', '데', '사', '겨', '도', '될까', '?'] new:  친구 의 전 여자 친구 가 좋 은 데 타 겨 도 될까 ? 
old: ['친구', '인데', '고백', '해도', '될까', '?'] new:  친구 인데 고백 해도 될까 ... 
old: ['친한', '동생', '인데', '짝', '남', '이', '되', '고', '있', '는', '느낌', '이', '에요', '.'] new:  친한 동생 인데 짝 남 이 되 고 없 는 느낌 이 에요 . 
old: ['친한', '동생', '인데', '짝', '녀', '가', '된', '것', '같', '아요', '.'] new:  None
old: ['친한', '동생', '인데', '짝사랑', '하', '는', '것', '같', '습니다', '.'] new:  친한 동생 인데 짝사랑 하 는 방법 같 습니다 . 
old: ['친한', '친구', '가', '저', '를', '좋아하', '는', '것', '같', '아요', '.'] new:  친한 친구 가 저 를 싫어하 는 것 같 아요 . 
old: ['친한', '친구', '의', '구', '남친', '이랑', '사귀', '어도', '될까요', '?'] new:  친한 친구 의 구 남친 이랑 사귀 더라도 될까요 ? 
old: ['친한', '친구', '의', '구', '여친', '이랑', '사귀', '어도'

14337

14337

In [42]:
#ans_corpus 만 증강
#aug_que_corpus = []
#aug_ans_corpus = []

for index in tqdm(range(len(ans_corpus))):
    new_src = lexical_sub(ans_corpus[index], wv_model)
    print("old:", ans_corpus[index], "new: ",new_src)
    if new_src is not None: 
        aug_ans_corpus.append(new_src.split())
        aug_que_corpus.append(que_corpus[index])
    # Augmentation이 없더라도 원본 문장을 포함시킵니다
    #aug_que_corpus.append(que_corpus[index])
    #aug_ans_corpus.append(ans_corpus[index])

#print(new_corpus[:10])
len(aug_que_corpus)
len(aug_ans_corpus)

  0%|          | 0/7731 [00:00<?, ?it/s]

old: ['하루', '가', '또', '가', '네요', '.'] new:  하루 가 또 가 군요 . 
old: ['위로', '해', '드립니다', '.'] new:  위로 해 드립니다 는데 
old: ['여행', '은', '언제나', '좋', '죠', '.'] new:  여행 은데 언제나 좋 죠 . 
old: ['눈살', '이', '찌푸려', '지', '죠', '.'] new:  None
old: ['다시', '새로', '사', '는', '게', '마음', '편해요', '.'] new:  곧바로 새로 사 는 게 마음 편해요 . 
old: ['잘', '모르', '고', '있', '을', '수', '도', '있', '어요', '.'] new:  잘 모르 고 있 을 수 때문 있 어요 . 
old: ['시간', '을', '정하', '고', '해', '보', '세요', '.'] new:  시간 를 정하 고 해 보 세요 . 
old: ['자랑', '하', '는', '자리', '니까요', '.'] new:  자랑 하 는 자리 ㄴ데요 . 
old: ['그', '사람', '도', '그럴', '거', '예요', '.'] new:  None
old: ['혼자', '를', '즐기', '세요', '.'] new:  혼자 를 즐기 세요 는데 
old: ['돈', '은', '다시', '들어올', '거', '예요', '.'] new:  None
old: ['땀', '을', '식혀', '주', '세요', '.'] new:  땀 을 식혀 주기도 세요 . 
old: ['어서', '잊', '고', '새', '출발', '하', '세요', '.'] new:  어서 잊어버리 고 새 출발 하 세요 . 
old: ['빨리', '집', '에', '돌아가', '서', '끄', '고', '나오', '세요', '.'] new:  천천히 집 에 돌아가 서 끄 고 나오 세요 . 
old: ['다음', '달', '에', '는', '더', '절약', '해', '봐요', '.'] new:  다음 달이 에 는 더 절약

old: ['지금', '처럼', '잘', '될', '거', '예요', '.'] new:  None
old: ['미래', '의', '배우자', '가', '달라져요', '.'] new:  미래 의 형제자매 가 달라져요 . 
old: ['공부', '는', '언제나', '좋', '죠', '.'] new:  공부 ㄴ다는 언제나 좋 죠 . 
old: ['공부', '하', '면', '더', '많', '은', '선택', '을', '할', '수', '있', '죠', '.'] new:  공부 하 ㄴ다면 더 많 은 선택 을 할 수 있 죠 . 
old: ['같이', '수다', '떨', '면서', '놀', '까요', '?'] new:  같이 수다 떨 며 놀 까요 ? 
old: ['나', '만', '의', '공부', '방법', '을', '찾아보', '세요', '.'] new:  나의 만 의 공부 방법 을 찾아보 세요 . 
old: ['지금', '도', '늦', '지', '않', '았', '어요', '.'] new:  지금 도 늦 지 않 아서 어요 . 
old: ['나', '한테', '맞', '는', '공부', '방법', '찾', '는', '게', '시급', '하', '네요', '.'] new:  나 한테 맞 는 공부 방법 찾아내 는 게 시급 하 네요 . 
old: ['잠시', '쉬', '어도', '돼요', '.'] new:  잠시 숀 어도 돼요 . 
old: ['좋', '은', '결과', '있', '을', '거', '예요', '!'] new:  좋 은 결과물 있 을 거 예요 ! 
old: ['잘', '될', '거', '예요', '.'] new:  잘 될 것 예요 . 
old: ['친구', '와', '같이', '가', '보', '세요', '.'] new:  친구 와도 같이 가 보 세요 . 
old: ['성향', '차이', '가', '좀', '있', '기', '는', '하', '죠', '.'] new:  성향 차이 가 좀 없 기 는 하 죠 . 
old: ['꾸준히', '약', '먹', '

old: ['조금', '만', '기다리', '면', '다시', '전기', '가', '들어올', '거', '예요', '.'] new:  조금 만 기다리 면 다시 직류 가 들어올 거 예요 . 
old: ['적당', '해요', '.'] new:  적당 해요 는데 
old: ['스스로', '단단', '해', '지', '세요', '.'] new:  스스로 단단 해 지 ㅂ시오 . 
old: ['제', '가', '드리', '고', '싶', '네요', '.'] new:  제 가 드리 고 싶 군요 . 
old: ['집안', '분위기', '가', '바뀔', '거', '예요', '.'] new:  집안 분위기 가 바뀔 거 예요 는데 
old: ['꽃', '선물', '은', '언제나', '좋', '죠', '.'] new:  꽃 선물 은데 언제나 좋 죠 . 
old: ['솜씨', '가', '좋', '으시', '네요', '.'] new:  솜씨 놀드 좋 으시 네요 . 
old: ['기분', '좋', '아', '보이', '세요', '.'] new:  표정 좋 아 보이 세요 . 
old: ['마음', '의', '안정', '을', '취하', '기', '좋', '은', '취미', '네요', '.'] new:  괴로움 의 안정 을 취하 기 좋 은 취미 네요 . 
old: ['벚꽃', '계절', '이', '다가왔', '네요', '.'] new:  벚꽃 연중 이 다가왔 네요 . 
old: ['거꾸로', '해서', '드라이플라워', '만들', '어', '보', '세요', '.'] new:  None
old: ['부러워요', '!'] new:  부러워요 캐치 
old: ['멋진', '선물', '이', '네요', '.'] new:  멋진 대접 이 네요 . 
old: ['센스', '있', '는', '선물', '이', '에요', '.'] new:  센스 없 는 선물 이 에요 . 
old: ['받', '는', '사람', '이', '부럽', '네요', '.'] new:  None
old: ['저', '도', 

old: ['잘', '하', '실', '거', '예요', '!'] new:  잘 하 실 것 예요 ! 
old: ['같이', '가요', '.'] new:  같이 가요 는데 
old: ['다', '잘', '될', '거', '예요', '.'] new:  으며 잘 될 거 예요 . 
old: ['같이', '놀', '아요', '.'] new:  같이 놀 아요 는데 
old: ['지금', '그러', '고', '있', '어요', '.'] new:  지금 그러 기에 있 어요 . 
old: ['잊어버리', '세요', '.'] new:  잊어버리 세요 는데 
old: ['상대방', '을', '이해', '해', '주', '세요', '.'] new:  상대방 을 파악 해 주 세요 . 
old: ['아무', '것', '도', '안', '해도', '괜찮', '아요', '.'] new:  아무 방법 도 안 해도 괜찮 아요 . 
old: ['상대방', '에게', '너무', '무거운', '짐', '을', '주', '지', '마세요', '.'] new:  상대방 에게 너무 무거운 짐 을 주 꼼짝 마세요 . 
old: ['기다리', '는', '동안', '많', '은', '생각', '이', '들', '었', '겠', '네요', '.'] new:  기다리 는 내내 많 은 생각 이 들 었 겠 네요 . 
old: ['그럴', '때', '마다', '따끔', '하', '게', '말', '해', '보', '세요', '.'] new:  그럴 때 마다 따끔 시키 게 말 해 보 세요 . 
old: ['상대방', '도', '미소', '짓', '게', '해', '주', '세요', '.'] new:  상대방 때문 미소 짓 게 해 주 세요 . 
old: ['지금', '모습', '도', '좋', '아요'] new:  현재 모습 도 좋 아요 
old: ['그런', '친구', '는', '거르', '세요', '.'] new:  이런 친구 는 거르 세요 . 
old: ['상종', '하', '지', '마세요', '.'] new: 

...

old: ['그', '사람', '에', '대한', '예의', '일', '것', '같', '아요', '.'] new:  그녀 사람 에 대한 예의 일 것 같 아요 . 
old: ['무슨', '이유', '가', '있', '을', '거', '예요', '.'] new:  무슨 취지 가 있 을 거 예요 . 
old: ['위로', '를', '해', '줘', '보', '세요', '.'] new:  None
old: ['곧', '사랑', '이', '찾아올', '거', '라', '믿', '어요', '.'] new:  곧 사랑 이 찾아올 거 라 믿 어요 는데 
old: ['공부', '도와', '달', '라고', '해', '보', '세요', '.'] new:  공부 도와 달 라고 해의 보 세요 . 
old: ['카톡', '해', '보', '세요', '.'] new:  카톡 해의 보 세요 . 
old: ['항상', '아쉬움', '이', '남', '는가', '봐요', '.'] new:  항상 아쉬움 이 남 습니까 봐요 . 
old: ['정말', '사랑', '하', '는', '분', '인가', '봐요', '.'] new:  정말로 사랑 하 는 분 인가 봐요 . 
old: ['놀랐', '겠', '어요', '.'] new:  None
old: ['가볍', '게', '밥', '먹', '고', '영화', '보', '는', '거', '어떨까', '요', '.'] new:  가볍 게 밥 먹 고 영화 보 ㄴ다는 거 어떨까 요 . 
old: ['항상', '후회', '만', '남', '나', '봐요', '.'] new:  항상 후회 만이 남 나 봐요 . 
old: ['좋', '은', '결실', '맺', '길', '바랍니다', '.'] new:  좋 은 결실 맺었 길 바랍니다 . 
old: ['어색', '한', '시간', '이', '었', '겠', '네요', '.'] new:  어색 한두 시간 이 었 겠 네요 . 
old: ['아쉽', '네요', '.'] new:  안타깝 네요 . 
old: ['잘', 

old: ['용기', '를', '내', '서', '고백', '해', '보', '는', '건', '어떨까', '요', '.'] new:  용기 를 내 서 고백 해 보 는 건과 어떨까 요 . 
old: ['사랑', '이', '내', '맘', '같', '지', '않', '아서', '그렇게', '되', '나', '봐요', '.'] new:  사랑 이 내 맘 같 지 않 아서 그렇게 이루어지 나 봐요 . 
old: ['생각', '처럼', '쉽', '지', '않', '지요', '.'] new:  생각 처럼 쉽 지 못하 지요 . 
old: ['끝', '을', '받아들이', '는', '것', '도', '필요', '합니다', '.'] new:  끝 을 알리 는 것 도 필요 합니다 . 
old: ['먼저', '연락', '해', '보', '는', '것', '도', '좋', '을', '것', '같', '습니다', '.'] new:  먼저 연락 해의 보 는 것 도 좋 을 것 같 습니다 . 
old: ['좋', '아', '하', '는', '건', '본인', '의', '자유', '지만', '많이', '힘들', '거', '예요', '.'] new:  좋 아 시키 는 건 본인 의 자유 지만 많이 힘들 거 예요 . 
old: ['저', '는', '짝사랑', '전공', '이', '에요', '.'] new:  저 는 짝사랑 전공 그러 에요 . 
old: ['나', '만', '좋', '아', '한다는', '사실', '이', '그렇게', '만들', '어요', '.'] new:  나 만이 좋 아 한다는 사실 이 그렇게 만들 어요 . 
old: ['해', '봤', '어요', '.'] new:  해 봤 어요 는데 
old: ['여기', '까지', '인연', '이', '었', '나', '봅니다', '.'] new:  여기 까 인연 이 었 나 봅니다 . 
old: ['마음', '이', '아프', '겠', '네요', '.'] new:  마음 그러 아프 겠 네요 . 
old: ['그래도', '좋', '아', '하

old: ['감동', '적', '인', '선물', '이', '될', '거', '같', '아요', '.'] new:  감동 적 인은 선물 이 될 거 같 아요 . 
old: ['가능', '한', '거', '같', '아요', '.'] new:  가능 한두 거 같 아요 . 
old: ['서로', '떨어져서', '그리워할', '시간', '을', '적당히', '만들', '어', '주', '는', '게', '관계', '를', '더', '깊', '게', '만들', '어', '주', '기', '도', '할', '거', '예요', '.'] new:  서로 떨어져서 그리워할 시간 를 적당히 만들 어 주 는 게 관계 를 더 깊 게 만들 어 주 기 도 할 거 예요 . 
old: ['뭐', '든', '함께', '하', '려는', '것', '도', '좋', '겠', '지만', '오래', '붙', '어', '잇', '는다고', '해서', '사랑', '이', '더', '커', '지', '거나', '깊', '어', '지', '지', '않', '아요', '.'] new:  뭐 든 함께 하 려는 것 도 좋 겠 지만 오래 붙 어 잇 는다고 해서 사랑 이 더 커 지 거나 깊 어 지 지 못하 아요 . 
old: ['귀찮', '아서', '친구', '랑', '하루', '종일', '연락', '안', '해요', '.'] new:  귀찮 아서 친구 랑 하루 하루 연락 안 해요 . 
old: ['그것', '또한', '감정', '의', '일부', '니까요', '.'] new:  그것 또한 감정 의 일부 ㄴ데요 . 
old: ['열심히', '갚', '아', '나가', '세요', '.'] new:  열심히 돌려받 아 나가 세요 . 
old: ['짝', '이', '라', '더', '좋', '겠', '네요', '.'] new:  짝 이 라 던 좋 겠 네요 . 
old: ['존경', '의', '의미', '라고', '생각', '하', '세요', '.'] new:  존경 인의 의미 라고 생각 하 세요 . 
old: ['우선'

21150

21150

In [44]:
list(zip(aug_que_corpus, aug_ans_corpus))

[(['12', '시가', '땡', '!'], ['하루', '가', '또', '가', '네요', '.']),
 (['12', '시', '땡', '!'], ['하루', '가', '또', '가', '네요', '.']),
 (['1', '지망', '학교', '떨어졌', '어'], ['위로', '해', '드립니다', '.']),
 (['3', '박', '4', '일', '놀', '러', '가', '고', '싶', '으며'],
  ['여행', '은', '언제나', '좋', '죠', '.']),
 (['3', '박', '4', '일', '놀', '러', '가', '고', '싶', '다'],
  ['여행', '은', '언제나', '좋', '죠', '.']),
 (['ppl', '강하', '네'], ['눈살', '이', '찌푸려', '지', '죠', '.']),
 (['ppl', '심하', '네'], ['눈살', '이', '찌푸려', '지', '죠', '.']),
 (['sd', '단말기', '망가졌', '어'], ['다시', '새로', '사', '는', '게', '마음', '편해요', '.']),
 (['sd', '카드', '망가졌', '어'], ['다시', '새로', '사', '는', '게', '마음', '편해요', '.']),
 (['sns', '맞', '팔', '과연', '안', '하', '지', 'ㅠㅠ'],
  ['잘', '모르', '고', '있', '을', '수', '도', '있', '어요', '.']),
 (['sns', '맞', '팔', '왜', '안', '하', '지', 'ㅠㅠ'],
  ['잘', '모르', '고', '있', '을', '수', '도', '있', '어요', '.']),
 (['sns', '시간', '낭비', '인', '거', '아', '으며', '매일', '하', '는', '중'],
  ['시간', '을', '정하', '고', '해', '보', '세요', '.']),
 (['sns', '시간', '낭비', '인', '거', '아', '는데', 

#### que_corpus,  ans_corpus  동시에 증강해 보기

In [32]:
aug_que_corpus = []
aug_ans_corpus = []

In [33]:
#que_corpus, ans_corpus 동시 증강
#aug_que_corpus = []
#aug_ans_corpus = []

for old_que, old_ans in tqdm(zip(que_corpus,ans_corpus)):
    new_que = lexical_sub(old_que, wv_model)
    new_ans = lexical_sub(old_ans, wv_model)
    print("old: ",old_que, "new: ",new_que)
    if (new_que is not None) & (new_ans is not None): 
        aug_que_corpus.append(new_que.split())
        aug_ans_corpus.append(new_ans.split())
    
    # Augmentation이 없더라도 원본 문장을 포함시킵니다
    #aug_que_corpus.append(old_que)
    #aug_ans_corpus.append(old_ans)

#print(aug_que_corpus[:10])
len(aug_que_corpus)
len(aug_ans_corpus)

0it [00:00, ?it/s]

old:  ['12', '시', '땡', '!'] new:  None
old:  ['1', '지망', '학교', '떨어졌', '어'] new:  None
old:  ['3', '박', '4', '일', '놀', '러', '가', '고', '싶', '다'] new:  3 박 4 일 놀 러 가 기에 싶 다 
old:  ['3', '박', '4', '일', '정도', '놀', '러', '가', '고', '싶', '다'] new:  3 김 4 일 정도 놀 러 가 고 싶 다 
old:  ['ppl', '심하', '네'] new:  ppl 심하 카나 
old:  ['sd', '카드', '망가졌', '어'] new:  None
old:  ['sd', '카드', '안', '돼'] new:  None
old:  ['sns', '맞', '팔', '왜', '안', '하', '지', 'ㅠㅠ'] new:  sns 맞 팔 왜 안 하 지 ... 
old:  ['sns', '시간', '낭비', '인', '거', '아', '는데', '매일', '하', '는', '중'] new:  None
old:  ['sns', '시간', '낭비', '인데', '자꾸', '보', '게', '됨'] new:  sns 시간 낭비 인데 자꾸 보 도록 됨 
old:  ['sns', '보', '면', '나', '만', '빼', '고', '다', '행복', '해', '보여'] new:  None
old:  ['가끔', '궁금', '해'] new:  가끔 궁금 해의 
old:  ['가끔', '뭐', '하', '는지', '궁금', '해'] new:  이따금 뭐 하 는지 궁금 해 
old:  ['가끔', '은', '혼자', '인', '게', '좋', '다'] new:  가끔 은 혼자 인 도록 좋 다 
old:  ['가난', '한', '자', '의', '설움'] new:  None
old:  ['가만', '있', '어도', '땀', '난다'] new:  가만 있 어도 오줌 난다 
old:  ['가상', '화폐', '쫄딱',

old:  ['결혼', '하', '면', '좋', '을까'] new:  재혼 하 면 좋 을까 
old:  ['결혼', '하', '면', '행복', '할까', '?'] new:  None
old:  ['결혼', '하', '면', '행복', '해', '?'] new:  결혼 하 면 행복 해 ... 
old:  ['결혼', '하', '면', '행복', '해질까', '?'] new:  결혼 시키 면 행복 해질까 ? 
old:  ['결혼', '할까'] new:  None
old:  ['결혼', '해도', '되', '나'] new:  결혼 보하이 되 나 
old:  ['결혼', '해도', '될까'] new:  None
old:  ['결혼', '해야', '하나'] new:  재혼 해야 하나 
old:  ['경쟁', '이', '너무', '치열', '해'] new:  경쟁 그러 너무 치열 해 
old:  ['계속', '공부', '해도', '될까'] new:  지속 공부 해도 될까 
old:  ['계속', '도전', '하', '는', '거', '귀찮', '아'] new:  계속 도전 하 는 것 귀찮 아 
old:  ['계속', '방학', '이', '면', '좋', '을', '텐데'] new:  None
old:  ['계속', '보', '고', '싶', '어'] new:  계속 살펴보 고 싶 어 
old:  ['계속', '보', '고', '싶', '으면', '어떡', '해', '?'] new:  None
old:  ['계속', '속', '이', '진짜', '안', '좋', '아'] new:  계속 아강 이 진짜 안 좋 아 
old:  ['계속', '엇갈리', '는', '느낌'] new:  계속 겹쳐지 는 느낌 
old:  ['계속', '학생', '하', '고', '싶', '어'] new:  지속 학생 하 고 싶 어 
old:  ['계속', '한숨', '만', '나와'] new:  None
old:  ['고', '3', '은', '공부', '만', '해야겠지', '.'] new: 

old:  ['그런', '말', '을', '왜', '하', '지'] new:  그런 말 를 왜 하 지 
old:  ['그런', '사람', '인가', '보다', '해야', '하나', '봐'] new:  그런 젊은이 인가 보다 해야 하나 봐 
old:  ['그런', '사람', '인갑다', '해야지'] new:  None
old:  ['그런', '친구', '아니', '었', '는데', '너무', '귀찮', '게', '하', '네'] new:  그런 친구 아니 었 으며 너무 귀찮 게 하 네 
old:  ['그렇게', '갈', '거', '면서'] new:  그렇게 갈 것 면서 
old:  ['그렇게', '오래', '살', '았', '는데', '도', '이해', '를', '못', '하', '겠', '어'] new:  그렇게 오랫동안 살 았 는데 도 이해 를 못 하 겠 어 
old:  ['그렇게', '할래'] new:  None
old:  ['그림', '잘', '그리', '고', '싶', '다'] new:  그림 많이 그리 고 싶 다 
old:  ['그림', '좀', '잘', '그렸', '으면', '좋', '겠', '다'] new:  그림 좀 잘 그렸 으면 좋 겠 으며 
old:  ['그만', '두', '고', '나오', '고', '싶', '어'] new:  그만 두 고 올라오 고 싶 어 
old:  ['그만', '먹', '어야', '하', '는데'] new:  그만 먹 여야 하 는데 
old:  ['그만', '살', '고', '싶', '어'] new:  그만 살 고 싶 어서 
old:  ['그저', '그런', '하루'] new:  그저 그런 일주일 
old:  ['근사', '한', '곳', '알', '아', '냈', '어'] new:  근사 한 곳 울 아 냈 어 
old:  ['근육', '있', '으면', '멋있', '을', '텐데'] new:  혈관 있 으면 멋있 을 텐데 
old:  ['금값', '알', '아', '?'] new:  금값 알 아서 ? 
old:  ['

old:  ['나', '모르', '는', '게', '왜', '이렇게', '많', '지'] new:  나 모르 는 게 왜 그렇게 많 지 
old:  ['나', '몰래', '사귀', '는', '거', '같', '애'] new:  나 몰래 사귀 는 것 같 애 
old:  ['나', '무시', '당한', '거', '같', '아'] new:  나 무시 당하 거 같 아 
old:  ['나', '무시', '하', '는', '거', '같', '아'] new:  나 무시 하 ㄴ다는 거 같 아 
old:  ['나', '무시', '하', '는', '사람', '어떻게', '해', '?'] new:  나 무시 하 는 사람 어떻게 해 ... 
old:  ['나', '무시', '하', '는', '사람', '짜증', '나'] new:  나 무시 시키 는 사람 짜증 나 
old:  ['나', '문제', '가', '많', '은', '거', '같', '아'] new:  나 문제점 가 많 은 거 같 아 
old:  ['나', '뭐', '하', '는', '거', '지'] new:  나 ... 하 는 거 지 
old:  ['나', '미팅', '한다', '!'] new:  나의 미팅 한다 ! 
old:  ['나', '바뀌', '고', '싶', '어'] new:  나 바뀌 고 겠 어 
old:  ['나', '바', '본', '인가', '봄'] new:  나 바 합본 인가 봄 
old:  ['나', '백수', '야'] new:  나의 백수 야 
old:  ['나', '버림', '받', '은', '거', '같', '아'] new:  나 버림 받 은데 거 같 아 
old:  ['나', '보이스', '피싱', '당한', '거', '같', '은데', '어떡', '해', '?'] new:  나 보이스 피싱 당한 거 같 은데 어떡 해의 ? 
old:  ['나', '비만', '이', '야'] new:  나 비만 그러 야 
old:  ['나', '사랑', '하', '니', '?'] new:  나 사랑 하 니 ... 


...

old:  ['짝', '녀', '와', '자연', '스럽', '게', '친해질', '수', '있', '는', '방법', '좀', '.'] new:  짝 녀 와 자연 스럽 게 친해질 가능성 있 는 방법 좀 . 
old:  ['짝', '녀', '의', '전', '남친', '이', '나', '탔', '났', '음', '.'] new:  짝 년 의 전 남친 이 나 탔 났 음 . 
old:  ['짝', '녀', '한테', '같이', '스터디', '하', '자고', '해도', '되', '나요', '?'] new:  짝 녀 한테 같이 스터디 시키 자고 해도 되 나요 ? 
old:  ['짝', '녀', '한테', '고백', '했', '는데', '미안', '하', '대', '.'] new:  짝 녀 한테 고백 했 으며 미안 하 대 . 
old:  ['짝', '녀', '한테', '고백', '했', '는데', '잘', '됐', '으면', '.'] new:  짝 녀 한테 고백 했 는데 잘 됐 으면 는데 
old:  ['짝', '녀', '한테', '고백', '했', '는데', '짝', '녀', '가', '오해', '하', '게', '해서', '너무', '미안', '하', '다네요', '.'] new:  짝 녀 한테 고백 했 는데 짝 녀 가 오해 시키 게 해서 너무 미안 하 다네요 . 
old:  ['짝', '녀', '한테', '공부', '가르쳐', '달', '라고', '해', '볼까'] new:  짝 녀 에게 공부 가르쳐 달 라고 해 볼까 
old:  ['짝', '녀', '한테', '라인', '왔', '는데', '뭐', '라고', '답장', '해야', '할지', '모르', '겠', '어', '.'] new:  None
old:  ['짝', '녀', '한테', '문자', '왔', '어', '.'] new:  짝 년 한테 문자 왔 어 . 
old:  ['짝', '녀', '한테', '실망', '했', '음', '.'] new:  짝 녀 한테 실망 했 음 는데 
old:  ['짝', '녀'

old:  ['첫', '사랑', '보', '고', '싶', '어'] new:  마지막 사랑 보 고 싶 어 
old:  ['첫', '사랑', '생각나'] new:  첫 슬픔 생각나 
old:  ['첫', '사랑', '생각나'] new:  첫 슬픔 생각나 
old:  ['첫', '사랑', '생각', '만', '해도', '아련', '해'] new:  첫 사랑 판단 만 해도 아련 해 
old:  ['첫', '사랑', '도', '내', '생각', '할까', '?'] new:  첫 슬픔 도 내 생각 할까 ? 
old:  ['첫', '사랑', '도', '내', '가', '보', '고', '싶', '을까', '?'] new:  첫 슬픔 도 내 가 보 고 싶 을까 ? 
old:  ['첫', '사랑', '을', '다시', '만났', '어', '.'] new:  첫 사랑 을 다시 만났 어서 . 
old:  ['첫', '사랑', '을', '추억', '해'] new:  첫 슬픔 을 추억 해 
old:  ['첫', '사랑', '이', '떠올라'] new:  None
old:  ['첫', '사랑', '인', '거', '같', '아'] new:  첫 사랑 인은 거 같 아 
old:  ['청첩장', '고르', '고', '있', '어'] new:  None
old:  ['청첩장', '골랐', '어'] new:  None
old:  ['청첩장', '누', '구', '주', '지', '?'] new:  청첩장 누 구 주 꼼짝 ? 
old:  ['청첩장', '누구', '한테', '주', '지', '?'] new:  청첩장 어디 한테 주 지 ? 
old:  ['청첩장', '누구', '한테', '줘야', '할지'] new:  청첩장 어디 한테 줘야 할지 
old:  ['청첩장', '돌리', '기', '귀찮', '아'] new:  청첩장 돌리 기 귀찮 아서 
old:  ['청첩장', '만들', '어야지'] new:  None
old:  ['청첩장', '을', '찍', '는', '날', '이', '오',

old:  ['헤어졌', '다가', '다시', '연애', '하', '는데', '잘', '사귈', '수', '있', '을까', '?'] new:  헤어졌 다가 다시 연애 하 는데 잘 사귈 수 없 을까 ? 
old:  ['헤어지', '고', '나', '서', '알', '았', '어', '사랑', '했', '다는', '걸'] new:  헤어지 고 나 서 알 아서 어 사랑 했 다는 걸 
old:  ['헤어지', '고', '얼마', '안', '됐', '는데', '썸', '타', '는', '거', '가능', '?'] new:  헤어지 고 얼마 안 됐 는데 썸 카 는 거 가능 ? 
old:  ['헤어진', '남친', '이랑', '다시', '썸', '타', '기'] new:  헤어진 남친 이랑 다시 썸 타 적기 
old:  ['헤어진', '여자', '친구', '랑', '썸', '부터', '시작', '할', '수', '있', '을까'] new:  헤어진 여자 친구 랑 썸 부터 시작 할 수 있 을까요 
old:  ['헬스', '장', '에서', '인사', '하', '는', '사람', '맘', '에', '드', '는데', '번호', '달', '라고', '할까', '?'] new:  헬스 장 에서 인사 하 는 젊은이 맘 에 드 는데 번호 달 라고 할까 ? 
old:  ['헬스', '장', '에서', '자주', '보', '는', '여자', '가', '보', '고', '싶', '어'] new:  헬스 장 에서 자주 보 는 여자 가 살펴보 고 싶 어 
old:  ['헷갈리', '는데', '유지', '하', '는', '게', '좋', '을까'] new:  헷갈리 는데 확보 하 는 게 좋 을까 
old:  ['현실', '적', '문제', '로', '연애', '포기', '해야', '할', '듯'] new:  현실 의식적 문제 로 연애 포기 해야 할 듯 
old:  ['혈액형', '이', '성격', '이랑', '무슨', '상관', '이', '지'] new:  간염 이 성격 이랑 무슨 상관 이 

8953

8953

In [34]:
#que_corpus, ans_corpus 동시 증강
aug_que_corpus_2 = []
aug_ans_corpus_2 = []

for old_que, old_ans in tqdm(zip(aug_que_corpus,aug_ans_corpus)):
    new_que = lexical_sub(old_que, wv_model)
    new_ans = lexical_sub(old_ans, wv_model)
    print("old: ",old_que, "new: ",new_que)
    if (new_que is not None) & (new_ans is not None): 
        aug_que_corpus_2.append(new_que.split())
        aug_ans_corpus_2.append(new_ans.split())
    
    # Augmentation이 없더라도 원본 문장을 포함시킵니다
    aug_que_corpus_2.append(old_que)
    aug_ans_corpus_2.append(old_ans)

#print(aug_que_corpus[:10])
len(aug_que_corpus_2)
len(aug_ans_corpus_2)

0it [00:00, ?it/s]

old:  ['3', '박', '4', '일', '놀', '러', '가', '기에', '싶', '다'] new:  3 박 4 일 놀 러 놀드 기에 싶 다 
old:  ['3', '김', '4', '일', '정도', '놀', '러', '가', '고', '싶', '다'] new:  3 김 4 일 정도 놀 러 가 고 겠 다 
old:  ['sns', '맞', '팔', '왜', '안', '하', '지', '...'] new:  sns 맞 팔 과연 안 하 지 ... 
old:  ['sns', '시간', '낭비', '인데', '자꾸', '보', '도록', '됨'] new:  sns 시간 낭비 인데 자꾸 보 게끔 됨 
old:  ['가끔', '궁금', '해의'] new:  가끔 궁금 해 
old:  ['이따금', '뭐', '하', '는지', '궁금', '해'] new:  이따금 뭐 하 다면 궁금 해 
old:  ['가끔', '은', '혼자', '인', '도록', '좋', '다'] new:  가끔 은데 혼자 인 도록 좋 다 
old:  ['가만', '있', '어도', '오줌', '난다'] new:  가만 있 어도 체액 난다 
old:  ['증기', '불', '켜', '고', '나갔', '어'] new:  None
old:  ['증기', '불', '켜', '놓', '고', '나온', '거', '같', '아'] new:  증기 불 켜지 놓 고 나온 거 같 아 
old:  ['가스', '빌', '너무', '많이', '나왔', '다', '.'] new:  가스 빌 너무 자주 나왔 다 . 
old:  ['가스', '비', '비싼데', '감기', '매달리', '겠', '어'] new:  가스 비 비싼데 감기 매달리 겠 어서 
old:  ['가스', '비', '욕설', '아님'] new:  가스 빌 욕설 아님 
old:  ['가장', '분명', '한', '건', '뭘까', '?'] new:  가장 분명 한 건과 뭘까 ? 
old:  ['가족', '여행', '가', '기', '로서', '

old:  ['공부', '계속', '보하이', '될까'] new:  가르치 계속 보하이 될까 
old:  ['가르치', '때려', '치워야', '하나'] new:  None
old:  ['공부', '시작', '보하이', '될까'] new:  가르치 시작 보하이 될까 
old:  ['공부', '잘', '시키', '고', '싶', '어'] new:  가르치 잘 시키 고 싶 어 
old:  ['공부', '조금', '더', '할', '걸'] new:  공부 약간 더 할 걸 
old:  ['공부', '시키', '기', '싫', '다'] new:  공부 시키 적기 싫 다 
old:  ['공부', '는', '내', '체질', '이', '아닌', '것', '같', '아서'] new:  공부 ㄴ다는 내 체질 이 아닌 것 같 아서 
old:  ['공부', '로', '먹', '고', '살', '가능성', '있', '을까'] new:  공부 로 먹 고 살 위험성 있 을까 
old:  ['가르치', '하', '기', '싫', '은', '날'] new:  가르치 시키 기 싫 은 날 
old:  ['공부', '시키', '는', '이유', '?'] new:  공부 꾀하 는 이유 ? 
old:  ['공부', '시키', '는', '이유', '가', '없', '어'] new:  공부 시키 는 이유 가 없었 어 
old:  ['공시', '준비', '어렵', '어'] new:  통지 준비 어렵 어 
old:  ['공시', '준비', '중의'] new:  공시 추진 중의 
old:  ['공시', '준비', '하', 'ㄴ다는', '데', '힘들', '다'] new:  공시 추진 하 ㄴ다는 데 힘들 다 
old:  ['공시', '생', '이', '야가'] new:  통지 생 이 야가 
old:  ['공연', '보', '고', '겠', '어'] new:  공연 보 고 겠 어서 
old:  ['콘서트', '보', '러', '가', '고', '싶', '어'] new:  콘서트 살펴보 러 가 고 싶 어 
ol

old:  ['꿈', '은데', '많', '은데'] new:  악몽 은데 많 은데 
old:  ['꿈', '이', '너무', '많', '아서'] new:  꿈 이 워낙 많 아서 
old:  ['꿈', '그러', '다양', '해'] new:  꿈 그러 다양 해의 
old:  ['꿈', '이', '다섯', '개', '야'] new:  꿈 이 여섯 개 야 
old:  ['악몽', '이', '자꾸', '바뀌', '어'] new:  악몽 이 그럼 바뀌 어 
old:  ['끝', '나', '니까', '합리', '하', '다'] new:  끝 나의 니까 합리 하 다 
old:  ['낌새', '가', '미만', '하', '더니', '딱', '걸렸', '어'] new:  낌새 가 미만 하 으니 딱 걸렸 어 
old:  ['낌새', '가', '있', '더니', '벌레', '걸렸', '어'] new:  None
old:  ['나', '감정', '쓰레기통', '이', '였', '나', '봐'] new:  나의 감정 쓰레기통 이 였 나 봐 
old:  ['나', '갖', '기에', '장난친', '건가'] new:  나의 갖 기에 장난친 건가 
old:  ['나', '같', '은', '사람', '은', '동물', '키우', '면', '안', '되', '싶', '지'] new:  나 같 은 사람 은 동물 키우 ㄴ다면 안 되 싶 지 
old:  ['나', '거짓말', '못하', '하', '겠', '어'] new:  나 거짓말 못하 하 싶 어 
old:  ['나', '결정', '많이', '한', '거', '지', '?'] new:  나의 결정 많이 한 거 지 ? 
old:  ['나', '결정', '했', '어서'] new:  나 의결 했 어서 
old:  ['나', '좋', '지', '않', '니'] new:  나 좋 꼼짝 않 니 
old:  ['나', '교직이수', '할', '가능성', '있', '을까', '?'] new:  나 교직이수 때때 가능성 있 을까 ? 
old:  ['나의', 

old:  ['나이', '때문', '에', '무시', '받', '아서', '어'] new:  나이 때문 에 배제 받 아서 어 
old:  ['나이', '어리', '다고', '배제', '해'] new:  나이 병들 다고 배제 해 
old:  ['나이', '놀드', '많', '은데', '취직', '이', '될까'] new:  나이 놀드 많 은데 진학 이 될까 
old:  ['나이', '도', '없', '으니', '영양제', '좀', '챙겨', '볼까'] new:  나이 도 없 으니 영양제 조금 챙겨 볼까 
old:  ['나이', '들', '면서', '눈물', '이', '많', '아', '졌', '어서'] new:  나이 부유층 면서 눈물 이 많 아 졌 어서 
old:  ['예전', '에', '뭐', '하고', '먹', '고', '사', '냐'] new:  예전 에 뭐 하고 먹 기에 사 냐 
old:  ['나', '한테', '감추', '는', '게', '한가지', '도', '없', '었', '으면'] new:  나 한테 감추 는 게 하나 도 없 었 으면 
old:  ['나의', '한테', '거짓말', '좀', '안', '했', '으면'] new:  None
old:  ['나', '한테', '너무', '많', '은', '걸', '바라', 'ㄴ다는', '듯'] new:  나의 한테 너무 많 은 걸 바라 ㄴ다는 듯 
old:  ['나의', '한테', '문제', '가', '많', '아'] new:  나의 한테 문제 놀드 많 아 
old:  ['나의', '한테', '상', '의', '좀', '하', '지'] new:  나의 한테 상 의 조금 하 지 
old:  ['나', '한테', '상의', '시키', '면', '좋', '을', '텐데'] new:  나의 한테 상의 시키 면 좋 을 텐데 
old:  ['나', '한테', '할', '말', '있', '회', '뭘까', '?'] new:  나 한테 할 말 있 회가 뭘까 ? 
old:  ['나의', '한테', '행운', '좀', 

...

old:  ['짝', '녀랑', '저녁', '에', '보', '기', '로', '했', '는데', '연락', '다섯', '절임', '.'] new:  짝 녀랑 저녁 이에 보 기 로 했 는데 연락 다섯 절임 . 
old:  ['짝', '녀랑', '조금', '이', '라도', '닮', '다면', '눈', '이', '가', '는', '듯', '.'] new:  짝 녀랑 조금 이 라도 닮 다면 눈 이 가 ㄴ다는 듯 . 
old:  ['짝', '녀랑', '카톡', '했', '더', '거', '다시', '읽', '어', '보', '는데', '거의', '다', '만', '물', '어', '보', '네', '.'] new:  짝 녀랑 카톡 했 더 거 다시 읽 어 보 는데 거의 다 만 물 어 보 카나 . 
old:  ['짝', '녀', '를', '반', '애', '들', '다', '알', '게', '공개', '적', '으로', '괜찮', '아', '하', '면', '싫', '어', '할까요', '?'] new:  짝 년 를 반 애 들 다 알 게 공개 적 으로 괜찮 아 하 면 싫 어 할까요 ? 
old:  ['짝', '녀', '한테', '남친', '이', '있', '었', '습니다', '.'] new:  짝 녀 한테 남친 이 있 였 습니다 . 
old:  ['짝', '녀', '에게', '다가가', '려면', '짝', '녀', '의', '연인', '에게', '먼저', '다가가', '는', '게', '나', '을까', '?'] new:  짝 녀 에게 다가가 려면 짝 녀 의 연인 에게 먼저 다가가 는 도록 나 을까 ? 
old:  ['짝', '녀', '와', '자연', '스럽', '게', '친해질', '가능성', '있', '는', '방법', '좀', '.'] new:  짝 녀 와 자연 스럽 도록 친해질 가능성 있 는 방법 좀 . 
old:  ['짝', '년', '의', '전', '남친', '이', '나', '탔', '났', '음', '.'] new:  짝 년 의 전 남친 이 나 탔 

old:  ['착각', '이', '면', '어떡', '해의'] new:  None
old:  ['착각', '일', '수', '도', '없', '는데', '서로', '좋아하', '는', '것', '같', '으면', '고백', '해', '?'] new:  착각 일 수 도 없 는데 서로 좋아하 는 것 같 으면 회개 해 ? 
old:  ['착해서', '잘', '해', '주', '는', '구걸', '좋', '아', '하', '는', '건지'] new:  착해서 잘 해 주 는 구걸 좋 아 시키 는 건지 
old:  ['착해서', '잘', '해', '주', '는', '건지', '괜찮', '아', '하', '는', '건지'] new:  착해서 잘 해 주 ㄴ다는 건지 괜찮 아 하 는 건지 
old:  ['참', '많이', '좋', '아', '했', '는데', '는데'] new:  None
old:  ['처음', '마음', '그러', '아픈', '게', '첫', '사랑', '인가'] new:  처음 마음 그러 아픈 게 첫 슬픔 인가 
old:  ['처음', '동성', '템', '으로', '어떤', '거', '를', '할까', '?'] new:  처음 동성 템 으로서 어떤 거 를 할까 ? 
old:  ['처음', '에', '는', '가벼운', '마음', '그러', '었', '는데'] new:  처음 이에 는 가벼운 마음 그러 었 는데 
old:  ['첫', '얼굴', '에', '반하', '는', '게', '가능', '해', '?'] new:  첫 얼굴 에 비하 는 게 가능 해 ? 
old:  ['첫', '눈', '에', '반하', 'ㄴ다는', '게', '가능', '해', '?'] new:  첫 눈 이에 반하 ㄴ다는 게 가능 해 ? 
old:  ['첫', '데이트', '이에', '뭐', '먹', '는', '걸', '좋', '을까', '?'] new:  마지막 데이트 이에 뭐 먹 는 걸 좋 을까 ? 
old:  ['첫', '만남', '에', '니스', '했', '는데', '너무', 

old:  ['간염', '이', '성격', '이랑', '무슨', '상관', '이', '지'] new:  간염 이 성격 이랑 무슨 상관 이 꼼짝 
old:  ['호감', '를', '표현', '하', '는', '방법'] new:  호감 를 표현 시키 는 방법 
old:  ['혼인', '신고', '아직', '못가', '했', '는데', '이혼', '해도', '될까'] new:  혼인 신고 아직 못가 했 으며 이혼 해도 될까 
old:  ['혼인', '신고', '하', '러', '왔', '어서'] new:  혼인 신고 하 ㄹ래 왔 어서 
old:  ['혼인', '신고', '하', '니까', '마음', '그러', '이상', '해'] new:  혼인 신고 하 길래 마음 그러 이상 해 
old:  ['혼자', '노력', '하', '는', '연애', '인은', '거', '같', '아'] new:  혼자 노력 하 는 연애 인은 것 같 아 
old:  ['혼자', '썸', '타', '는', '기분', '이', '야', '는데'] new:  거기 썸 타 는 기분 이 야 는데 
old:  ['혼자', '좋아하', 'ㄴ다는', '것', '같', '아'] new:  혼자 싫어하 ㄴ다는 것 같 아 
old:  ['나', '만', '좋', '아서', '하', '는', '것', '같', '아'] new:  나 만 좋 아 하 는 것 같 아 
old:  ['혼자', '싫어하', '는', '이야기', '들', '어', '볼래요', '?'] new:  혼자 좋아하 는 이야기 들 어 볼래요 ? 
old:  ['혼자', '좋아하', 'ㄴ다는', '이야기', '.'] new:  거기 좋아하 ㄴ다는 이야기 . 
old:  ['거기', '좋아하', '는', '게', '이렇게', '힘든', '적', '은', '처음', '이', '에요', '.'] new:  거기 좋아하 는 게 이렇게 힘든 적 은 처음 이 에요 는데 
old:  ['혼자', '가', '편하', '다는', '짝', '남의', '에게', '먼저'

16165

16165

In [35]:
que_corpus += aug_que_corpus_2 
ans_corpus += aug_ans_corpus_2 
len(que_corpus)
len(ans_corpus)

27988

27988

In [36]:
#list(zip(que_corpus, ans_corpus))
que_corpus[:3]
ans_corpus[:3]

[['12', '시', '땡', '!'],
 ['1', '지망', '학교', '떨어졌', '어'],
 ['3', '박', '4', '일', '놀', '러', '가', '고', '싶', '다']]

[['하루', '가', '또', '가', '네요', '.'],
 ['위로', '해', '드립니다', '.'],
 ['여행', '은', '언제나', '좋', '죠', '.']]

## Step 5. 데이터 벡터화

1. 위 소스를 참고하여 타겟 데이터 전체에 <start> 토큰과 <end> 토큰을 추가해 주세요!
2. 특수 토큰을 더함으로써 ans_corpus 또한 완성이 되었으니, que_corpus 와 결합하여 전체 데이터에 대한 단어 사전을 구축하고 벡터화하여 enc_train 과 dec_train 을 얻으세요!

In [37]:
#que_corpus = new_ques.copy()
len(que_corpus)

27988

In [38]:
#ans_corpus = []
#for ans in new_answ:
#    ans = ["<start>"] + ans + ["<end>"]
#    ans_corpus.append(ans)
    
for index in range(len(ans_corpus)):
    ans_corpus[index] = ["<start>"] + ans_corpus[index] + ["<end>"]

In [39]:
len(ans_corpus)
ans_corpus[0]

27988

['<start>', '하루', '가', '또', '가', '네요', '.', '<end>']

#### 단어 집합 생성

In [40]:
#vocab_size = 7881
#vocab_size = 7477
#tokenizer = tf.keras.preprocessing.text.Tokenizer(filters='',oov_token='<unk>',num_words=vocab_size)
tokenizer = tf.keras.preprocessing.text.Tokenizer(filters='',oov_token='<unk>')
tokenizer.fit_on_texts(que_corpus+ans_corpus)
enc_tensor = tokenizer.texts_to_sequences(que_corpus)
dec_tensor = tokenizer.texts_to_sequences(ans_corpus)

MAX_LEN = sequence_len + 2 # 41
enc_tensor = tf.keras.preprocessing.sequence.pad_sequences(enc_tensor, padding='post',maxlen=MAX_LEN)
dec_tensor = tf.keras.preprocessing.sequence.pad_sequences(dec_tensor, padding='post',maxlen=MAX_LEN)

print("vocab size:", len(tokenizer.index_word)+1)

vocab size: 8325


In [41]:
len(tokenizer.index_word)
tokenizer.index_word[7477]
vocab_size = len(tokenizer.index_word) + 1
vocab_size
tokenizer.index_word

8324

'베이'

8325

{1: '<unk>',
 2: '.',
 3: '<start>',
 4: '<end>',
 5: '이',
 6: '하',
 7: '는',
 8: '을',
 9: '세요',
 10: '가',
 11: '고',
 12: '좋',
 13: '어',
 14: '는데',
 15: '해',
 16: '있',
 17: '보',
 18: '거',
 19: '은',
 20: '지',
 21: '?',
 22: '아',
 23: '도',
 24: '게',
 25: '나',
 26: '겠',
 27: '에',
 28: '사람',
 29: '를',
 30: '예요',
 31: '싶',
 32: '어요',
 33: '없',
 34: '같',
 35: '것',
 36: '죠',
 37: '다',
 38: '한',
 39: '사랑',
 40: '네요',
 41: '면',
 42: '수',
 43: '안',
 44: '친구',
 45: '네',
 46: '아요',
 47: '의',
 48: '생각',
 49: '잘',
 50: '말',
 51: '않',
 52: '봐요',
 53: '할',
 54: '그러',
 55: '마음',
 56: '되',
 57: '주',
 58: '너무',
 59: '더',
 60: '했',
 61: '기',
 62: '만',
 63: '내',
 64: '일',
 65: '었',
 66: '들',
 67: '시키',
 68: '남자',
 69: '여자',
 70: '연락',
 71: '많이',
 72: 'ㄴ다는',
 73: '괜찮',
 74: '이별',
 75: '힘들',
 76: '해요',
 77: '시간',
 78: '어서',
 79: '한테',
 80: '에요',
 81: '은데',
 82: '으면',
 83: '썸',
 84: '먹',
 85: '에서',
 86: '때',
 87: '남',
 88: '저',
 89: '짝',
 90: 'ㅂ시오',
 91: '놀드',
 92: '았',
 93: '야',
 94: '으로',
 95: '으며',
 96: '길'

In [42]:
enc_tensor.shape
dec_tensor.shape

(27988, 41)

(27988, 41)

In [43]:
BATCH_SIZE = 32
train_dataset = tf.data.Dataset.from_tensor_slices((enc_tensor, dec_tensor)).batch(batch_size=BATCH_SIZE)

## Step 6. Transformer 모델 설계

### Positional Encoding

In [44]:
# Positional Encoding 구현
def positional_encoding(pos, d_model):
    def cal_angle(position, i):
        return position / np.power(10000, (2*(i//2)) / np.float32(d_model))

    def get_posi_angle_vec(position):
        return [cal_angle(position, i) for i in range(d_model)]

    sinusoid_table = np.array([get_posi_angle_vec(pos_i) for pos_i in range(pos)])

    sinusoid_table[:, 0::2] = np.sin(sinusoid_table[:, 0::2])
    sinusoid_table[:, 1::2] = np.cos(sinusoid_table[:, 1::2])

    return sinusoid_table

### MASK 생성

In [45]:
# Mask  생성하기
def generate_padding_mask(seq):
    seq = tf.cast(tf.math.equal(seq, 0), tf.float32)
    return seq[:, tf.newaxis, tf.newaxis, :]

def generate_lookahead_mask(size):
    mask = 1 - tf.linalg.band_part(tf.ones((size, size)), -1, 0)
    return mask

def generate_masks(src, tgt):
    enc_mask = generate_padding_mask(src)
    dec_enc_mask = generate_padding_mask(src)

    dec_lookahead_mask = generate_lookahead_mask(tgt.shape[1])
    dec_tgt_padding_mask = generate_padding_mask(tgt)
    dec_mask = tf.maximum(dec_tgt_padding_mask, dec_lookahead_mask)

    return enc_mask, dec_enc_mask, dec_mask

### Multi-head Attention

In [46]:
# Multi Head Attention 구현
class MultiHeadAttention(tf.keras.layers.Layer):
    def __init__(self, d_model, num_heads):
        super(MultiHeadAttention, self).__init__()
        self.num_heads = num_heads
        self.d_model = d_model
        
        self.depth = d_model // self.num_heads
        
        self.W_q = tf.keras.layers.Dense(d_model)
        self.W_k = tf.keras.layers.Dense(d_model)
        self.W_v = tf.keras.layers.Dense(d_model)
        
        self.linear = tf.keras.layers.Dense(d_model)

    def scaled_dot_product_attention(self, Q, K, V, mask):
        d_k = tf.cast(K.shape[-1], tf.float32)
        QK = tf.matmul(Q, K, transpose_b=True)

        scaled_qk = QK / tf.math.sqrt(d_k)

        if mask is not None: scaled_qk += (mask * -1e9)  

        attentions = tf.nn.softmax(scaled_qk, axis=-1)
        out = tf.matmul(attentions, V)

        return out, attentions
        

    def split_heads(self, x):
        bsz = x.shape[0]
        split_x = tf.reshape(x, (bsz, -1, self.num_heads, self.depth))
        split_x = tf.transpose(split_x, perm=[0, 2, 1, 3])

        return split_x

    def combine_heads(self, x):
        bsz = x.shape[0]
        combined_x = tf.transpose(x, perm=[0, 2, 1, 3])
        combined_x = tf.reshape(combined_x, (bsz, -1, self.d_model))

        return combined_x

    
    def call(self, Q, K, V, mask):
        WQ = self.W_q(Q)
        WK = self.W_k(K)
        WV = self.W_v(V)
        
        WQ_splits = self.split_heads(WQ)
        WK_splits = self.split_heads(WK)
        WV_splits = self.split_heads(WV)
        
        out, attention_weights = self.scaled_dot_product_attention(
            WQ_splits, WK_splits, WV_splits, mask)
                        
        out = self.combine_heads(out)
        out = self.linear(out)
            
        return out, attention_weights

### Position-wise Feed Forward Network

In [47]:
# Position-wise Feed Forward Network 구현
class PoswiseFeedForwardNet(tf.keras.layers.Layer):
    def __init__(self, d_model, d_ff):
        super(PoswiseFeedForwardNet, self).__init__()
        self.d_model = d_model
        self.d_ff = d_ff

        self.fc1 = tf.keras.layers.Dense(d_ff, activation='relu')
        self.fc2 = tf.keras.layers.Dense(d_model)

    def call(self, x):
        out = self.fc1(x)
        out = self.fc2(out)
            
        return out

### Encoder Layer

In [48]:
# Encoder의 레이어 구현
class EncoderLayer(tf.keras.layers.Layer):
    def __init__(self, d_model, n_heads, d_ff, dropout):
        super(EncoderLayer, self).__init__()

        self.enc_self_attn = MultiHeadAttention(d_model, n_heads)
        self.ffn = PoswiseFeedForwardNet(d_model, d_ff)

        self.norm_1 = tf.keras.layers.LayerNormalization(epsilon=1e-6)
        self.norm_2 = tf.keras.layers.LayerNormalization(epsilon=1e-6)

        self.do = tf.keras.layers.Dropout(dropout)
        
    def call(self, x, mask):
        '''
        Multi-Head Attention
        '''
        residual = x
        out = self.norm_1(x)
        out, enc_attn = self.enc_self_attn(out, out, out, mask)
        out = self.do(out)
        out += residual
        
        '''
        Position-Wise Feed Forward Network
        '''
        residual = out
        out = self.norm_2(out)
        out = self.ffn(out)
        out = self.do(out)
        out += residual
        
        return out, enc_attn

### Decoder Layer

In [49]:
# Decoder 레이어 구현
class DecoderLayer(tf.keras.layers.Layer):
    def __init__(self, d_model, num_heads, d_ff, dropout):
        super(DecoderLayer, self).__init__()

        self.dec_self_attn = MultiHeadAttention(d_model, num_heads)
        self.enc_dec_attn = MultiHeadAttention(d_model, num_heads)

        self.ffn = PoswiseFeedForwardNet(d_model, d_ff)

        self.norm_1 = tf.keras.layers.LayerNormalization(epsilon=1e-6)
        self.norm_2 = tf.keras.layers.LayerNormalization(epsilon=1e-6)
        self.norm_3 = tf.keras.layers.LayerNormalization(epsilon=1e-6)

        self.do = tf.keras.layers.Dropout(dropout)
    
    def call(self, x, enc_out, dec_enc_mask, padding_mask):
        '''
        Masked Multi-Head Attention
        '''
        residual = x
        out = self.norm_1(x)
        out, dec_attn = self.dec_self_attn(out, out, out, padding_mask)
        out = self.do(out)
        out += residual

        '''
        Multi-Head Attention
        '''
        residual = out
        out = self.norm_2(out)
        # Q, K, V 순서에 주의하세요!
        out, dec_enc_attn = self.enc_dec_attn(Q=out, K=enc_out, V=enc_out, mask=dec_enc_mask)
        out = self.do(out)
        out += residual
        
        '''
        Position-Wise Feed Forward Network
        '''
        residual = out
        out = self.norm_3(out)
        out = self.ffn(out)
        out = self.do(out)
        out += residual

        return out, dec_attn, dec_enc_attn

### Encoder

In [50]:
# Encoder 구현
class Encoder(tf.keras.Model):
    def __init__(self,
                    n_layers,
                    d_model,
                    n_heads,
                    d_ff,
                    dropout):
        super(Encoder, self).__init__()
        self.n_layers = n_layers
        self.enc_layers = [EncoderLayer(d_model, n_heads, d_ff, dropout) 
                        for _ in range(n_layers)]
    
        self.do = tf.keras.layers.Dropout(dropout)
        
    def call(self, x, mask):
        out = x
    
        enc_attns = list()
        for i in range(self.n_layers):
            out, enc_attn = self.enc_layers[i](out, mask)
            enc_attns.append(enc_attn)
        
        return out, enc_attns

### Decoder

In [51]:
# Decoder 구현
class Decoder(tf.keras.Model):
    def __init__(self,
                    n_layers,
                    d_model,
                    n_heads,
                    d_ff,
                    dropout):
        super(Decoder, self).__init__()
        self.n_layers = n_layers
        self.dec_layers = [DecoderLayer(d_model, n_heads, d_ff, dropout) 
                            for _ in range(n_layers)]
                            
    def call(self, x, enc_out, dec_enc_mask, padding_mask):
        out = x
    
        dec_attns = list()
        dec_enc_attns = list()
        for i in range(self.n_layers):
            out, dec_attn, dec_enc_attn = \
            self.dec_layers[i](out, enc_out, dec_enc_mask, padding_mask)

            dec_attns.append(dec_attn)
            dec_enc_attns.append(dec_enc_attn)

        return out, dec_attns, dec_enc_attns

### Transformer 전체 모델 조립

In [52]:
class Transformer(tf.keras.Model):
    def __init__(self,
                    n_layers,
                    d_model,
                    n_heads,
                    d_ff,
                    src_vocab_size,
                    tgt_vocab_size,
                    pos_len,
                    dropout=0.2,
                    shared_fc=True,
                    shared_emb=False):
        super(Transformer, self).__init__()
        
        self.d_model = tf.cast(d_model, tf.float32)

        if shared_emb:
            self.enc_emb = self.dec_emb = \
            tf.keras.layers.Embedding(src_vocab_size, d_model)
        else:
            self.enc_emb = tf.keras.layers.Embedding(src_vocab_size, d_model)
            self.dec_emb = tf.keras.layers.Embedding(tgt_vocab_size, d_model)

        self.pos_encoding = positional_encoding(pos_len, d_model)
        self.do = tf.keras.layers.Dropout(dropout)

        self.encoder = Encoder(n_layers, d_model, n_heads, d_ff, dropout)
        self.decoder = Decoder(n_layers, d_model, n_heads, d_ff, dropout)

        self.fc = tf.keras.layers.Dense(tgt_vocab_size)

        self.shared_fc = shared_fc

        if shared_fc:
            self.fc.set_weights(tf.transpose(self.dec_emb.weights))

    def embedding(self, emb, x):
        seq_len = x.shape[1]

        out = emb(x)

        if self.shared_fc: out *= tf.math.sqrt(self.d_model)

        out += self.pos_encoding[np.newaxis, ...][:, :seq_len, :]
        out = self.do(out)

        return out

        
    def call(self, enc_in, dec_in, enc_mask, dec_enc_mask, dec_mask):
        enc_in = self.embedding(self.enc_emb, enc_in)
        dec_in = self.embedding(self.dec_emb, dec_in)

        enc_out, enc_attns = self.encoder(enc_in, enc_mask)
        
        dec_out, dec_attns, dec_enc_attns = \
        self.decoder(dec_in, enc_out, dec_enc_mask, dec_mask)
        
        logits = self.fc(dec_out)
        
        return logits, enc_attns, dec_attns, dec_enc_attns

### 모델 인스턴스 생성

* Encoder와 Decoder 각각의 Embedding과 출력층의 Linear, 총 3개의 레이어가 Weight 공유

#### 시도 1

In [161]:
# Hyperparameters
n_layers = 2
d_model = 128 
n_heads = 4 # int(8/2)
d_ff = 512 # int(2048/2)
src_vocab_size = vocab_size # 7478
tgt_vocab_size = vocab_size # 7478
pos_len = sequence_len + 2  # MAX_LEN = 41
dropout = 0.2


transformer = Transformer(
    n_layers=n_layers,
    d_model=d_model,
    n_heads=n_heads,
    d_ff=d_ff,
    src_vocab_size=vocab_size,
    tgt_vocab_size=vocab_size,
    pos_len=pos_len,
    dropout=dropout,
    shared_fc=True,
    shared_emb=True)


#### 시도 2

In [129]:
# Hyperparameters
n_layers = 2
d_model = 128 
n_heads = 4 # int(8/2)
d_ff = 512 # int(2048/2)
src_vocab_size = vocab_size # 7478
tgt_vocab_size = vocab_size # 7478
pos_len = sequence_len + 2  # MAX_LEN = 41
dropout = 0.4


transformer = Transformer(
    n_layers=n_layers,
    d_model=d_model,
    n_heads=n_heads,
    d_ff=d_ff,
    src_vocab_size=vocab_size,
    tgt_vocab_size=vocab_size,
    pos_len=pos_len,
    dropout=dropout,
    shared_fc=True,
    shared_emb=True)

#### 시도 3

In [162]:
# Hyperparameters
n_layers = 2
d_model = 64 
n_heads = 4 
d_ff = 512 
src_vocab_size = vocab_size # 7478
tgt_vocab_size = vocab_size # 7478
pos_len = sequence_len + 2  # MAX_LEN = 41
dropout = 0.3


transformer = Transformer(
    n_layers=n_layers,
    d_model=d_model,
    n_heads=n_heads,
    d_ff=d_ff,
    src_vocab_size=vocab_size,
    tgt_vocab_size=vocab_size,
    pos_len=pos_len,
    dropout=dropout,
    shared_fc=True,
    shared_emb=True)

In [ ]:
# Hyperparameters
n_layers = 2
d_model = 64 
n_heads = 4 
d_ff = 512 
src_vocab_size = vocab_size # 7478
tgt_vocab_size = vocab_size # 7478
pos_len = sequence_len + 2  # MAX_LEN = 41
dropout = 0.3


transformer = Transformer(
    n_layers=n_layers,
    d_model=d_model,
    n_heads=n_heads,
    d_ff=d_ff,
    src_vocab_size=vocab_size,
    tgt_vocab_size=vocab_size,
    pos_len=pos_len,
    dropout=dropout,
    shared_fc=True,
    shared_emb=True)

## Step 7. 훈련하기

### Learning Rate Scheduler

In [150]:
# Learning Rate Scheduler 구현
class LearningRateScheduler(tf.keras.optimizers.schedules.LearningRateSchedule):
    def __init__(self, d_model, warmup_steps=4000):
        super(LearningRateScheduler, self).__init__()
        
        self.d_model = d_model
        self.warmup_steps = warmup_steps
    
    def __call__(self, step):
        arg1 = step ** -0.5
        arg2 = step * (self.warmup_steps ** -1.5)
        
        return (self.d_model ** -0.5) * tf.math.minimum(arg1, arg2)

### Learning Rate & Optimizer

In [151]:
# Learning Rate 인스턴스 선언 & Optimizer 구현
learning_rate = LearningRateScheduler(d_model)

optimizer = tf.keras.optimizers.Adam(learning_rate,
                                        beta_1=0.9,
                                        beta_2=0.98, 
                                        epsilon=1e-9)

### Loss Function

In [152]:
# Loss Function 정의
loss_object = tf.keras.losses.SparseCategoricalCrossentropy(
    from_logits=True, reduction='none')

def loss_function(real, pred):
    mask = tf.math.logical_not(tf.math.equal(real, 0))
    loss_ = loss_object(real, pred)

    mask = tf.cast(mask, dtype=loss_.dtype)
    loss_ *= mask

    return tf.reduce_sum(loss_)/tf.reduce_sum(mask)

### Train Step 정의

In [153]:
# Train Step 정의
@tf.function()
def train_step(src, tgt, model, optimizer):
    tgt_in = tgt[:, :-1]  # Decoder의 input
    gold = tgt[:, 1:]     # Decoder의 output과 비교하기 위해 right shift를 통해 생성한 최종 타겟

    enc_mask, dec_enc_mask, dec_mask = generate_masks(src, tgt_in)

    with tf.GradientTape() as tape:
        predictions, enc_attns, dec_attns, dec_enc_attns = \
        model(src, tgt_in, enc_mask, dec_enc_mask, dec_mask)
        loss = loss_function(gold, predictions)

    gradients = tape.gradient(loss, model.trainable_variables)    
    optimizer.apply_gradients(zip(gradients, model.trainable_variables))

    return loss, enc_attns, dec_attns, dec_enc_attns

### 훈련 & 평가

In [154]:
# 예문
#1. 지루하다, 놀러가고 싶어.
#2. 오늘 일찍 일어났더니 피곤하다.
#3. 간만에 여자친구랑 데이트 하기로 했어.
#4. 집에 있는다는 소리야.

#---

# 제출

#Translations
#> 1. 잠깐 쉬 어도 돼요 . <end>
#> 2. 맛난 거 드세요 . <end>
#> 3. 떨리 겠 죠 . <end>
#> 4. 좋 아 하 면 그럴 수 있 어요 . <end>

#Hyperparameters
#> n_layers: 1
#> d_model: 368
#> n_heads: 8
#> d_ff: 1024
#> dropout: 0.2

#Training Parameters
#> Warmup Steps: 1000
#> Batch Size: 64
#> Epoch At: 10

In [155]:
# 번역 생성 함수

def evaluate(sentence, model, src_tokenizer, tgt_tokenizer):
    sentence = preprocess_sentence(sentence)
    
    tokenizer = Mecab()
    pieces = tokenizer.morphs(sentence)    
    tokens = src_tokenizer.texts_to_sequences([pieces])
    #print(pieces, tokens)
    #print("morphs 토큰화: ",pieces)

    _input = tf.keras.preprocessing.sequence.pad_sequences(tokens,
                                                           maxlen=pos_len,
                                                           padding='post')
    #print("_input:", _input)
    
    ids = []
    output = tf.expand_dims([tgt_tokenizer.word_index['<start>']], 0)
    for i in range(dec_tensor.shape[-1]):
        enc_padding_mask, combined_mask, dec_padding_mask = \
        generate_masks(_input, output)

        predictions, enc_attns, dec_attns, dec_enc_attns =\
        model(_input, 
              output,
              enc_padding_mask,
              combined_mask,
              dec_padding_mask)

        predicted_id = \
        tf.argmax(tf.math.softmax(predictions, axis=-1)[0, -1]).numpy().item()

        if tgt_tokenizer.word_index['<end>'] == predicted_id:
            result = tgt_tokenizer.sequences_to_texts([ids])
            result = tgt_tokenizer.sequences_to_texts([ids])[0]
            #result = " ".join(result)
            #print(result)
            return pieces, result, enc_attns, dec_attns, dec_enc_attns

        ids.append(predicted_id)
        output = tf.concat([output, tf.expand_dims([predicted_id], 0)], axis=-1)

    #result = tgt_tokenizer.sequences_to_texts([ids])
    result = tgt_tokenizer.sequences_to_texts([ids])[0]
    #result = " ".join(result)
    #print(result)
    return pieces, result, enc_attns, dec_attns, dec_enc_attns

In [156]:
# 번역 생성
def translate_eval(sentence, model, src_tokenizer, tgt_tokenizer):

    pieces, result, enc_attns, dec_attns, dec_enc_attns = \
    evaluate(sentence, model, src_tokenizer, tgt_tokenizer)
    
    print('*** Question : %s' % (sentence))
    print('*** Predicted Answer : {}'.format(result))
    print('\n')


In [147]:
# test
translate_eval('지루하다, 놀러가고 싶어.', transformer, tokenizer, tokenizer)

*** Question : 지루하다, 놀러가고 싶어.
*** Predicted Answer : 센스 해로워 해로워 해로워 일지 장동 별 쏟 해로워 고프 일지 일지 일지 일지 을까요 해로워 해로워 해로워 일지 을까요 고프 을까요 격노 을까요 격노 고프 을까요 고프 을까요 고프 을까요 일지 격노 찔러 내 해로워 일지 을까요 센스 을까요 을까요




#### test 예문

In [157]:
questions = [
            "지루하다, 놀러가고 싶어.",
            "오늘 일찍 일어났더니 피곤하다.",
            "간만에 여자친구랑 데이트 하기로 했어.",
            "집에 있는다는 소리야."
]

answers = [
            "잠깐 쉬 어도 돼요 .",
            "맛난 거 드세요 .",
            "떨리 겠 죠.",
            "좋 아 하 면 그럴 수 있 어요 ."
]

#### 시도 1

In [128]:
# Hyperparameters
print(f"Hyperparameters \n \
      n_layers={n_layers} \n \
      d_model={d_model} \n \
      n_heads={n_heads} \n \
      d_ff={d_ff} \n \
      src_vocab_size={src_vocab_size} \n \
      tgt_vocab_size={tgt_vocab_size} \n \
      pos_len = {pos_len} \n \
      dropout={dropout}")

print(f"Training Parameters \n \
      Warmup Steps={4000} \n \
      BATCH_SIZE={BATCH_SIZE}")


EPOCHS = 10

for epoch in range(EPOCHS):
    total_loss = 0
    
    dataset_count = tf.data.experimental.cardinality(train_dataset).numpy()
    tqdm_bar = tqdm(total=dataset_count)
    for step, (enc_batch, dec_batch) in enumerate(train_dataset):
        batch_loss, enc_attns, dec_attns, dec_enc_attns = \
        train_step(enc_batch,
                    dec_batch,
                    transformer,
                    optimizer)

        total_loss += batch_loss
        
        tqdm_bar.set_description_str('Epoch %2d' % (epoch + 1))
        tqdm_bar.set_postfix_str('Loss %.4f' % (total_loss.numpy() / (step + 1)))
        a = tqdm_bar.update()
        
    for question in questions:
        translate_eval(question, transformer, tokenizer, tokenizer)
        
    
#    eval_bleu(transformer, questions, answers, tokenizer, tokenizer, verbose=True)

Hyperparameters 
       n_layers=2 
       d_model=128 
       n_heads=4 
       d_ff=512 
       src_vocab_size=8325 
       tgt_vocab_size=8325 
       pos_len = 41 
       dropout=0.2
Training Parameters 
       Warmup Steps=4000 
       BATCH_SIZE=32


  0%|          | 0/875 [00:00<?, ?it/s]

*** Question : 지루하다, 놀러가고 싶어.
*** Predicted Answer : 사랑 을 마음 을 것 같 아요 .


*** Question : 오늘 일찍 일어났더니 피곤하다.
*** Predicted Answer : 사랑 을 마음 을 게 좋 겠 네요 .


*** Question : 간만에 여자친구랑 데이트 하기로 했어.
*** Predicted Answer : 사랑 을 마음 을 게 좋 겠 네요 .


*** Question : 집에 있는다는 소리야.
*** Predicted Answer : 사랑 을 만 하 는 게 좋 겠 네요 .




  0%|          | 0/875 [00:00<?, ?it/s]

*** Question : 지루하다, 놀러가고 싶어.
*** Predicted Answer : 짝사랑 이 좋 아 하 는 것 도 좋 을 거 예요 .


*** Question : 오늘 일찍 일어났더니 피곤하다.
*** Predicted Answer : 짝사랑 이 에요 는데


*** Question : 간만에 여자친구랑 데이트 하기로 했어.
*** Predicted Answer : 짝사랑 이 네요 는데


*** Question : 집에 있는다는 소리야.
*** Predicted Answer : 짝사랑 이 좋 아 하 는 것 도 좋 을 거 같 아요 .




...

*** Question : 지루하다, 놀러가고 싶어.
*** Predicted Answer : 같이 살 자고 살 자고 해 보 세요 .


*** Question : 오늘 일찍 일어났더니 피곤하다.
*** Predicted Answer : 그것 만큼 정식 때문 공식적 처럼 기대 를 갈라 짓 을 갈라 봅니다 .


*** Question : 간만에 여자친구랑 데이트 하기로 했어.
*** Predicted Answer : 추억 으로 남기 ㄴ다는 편 이 좋 겠 어요 .


*** Question : 집에 있는다는 소리야.
*** Predicted Answer : 어디 에서 이나 나 봅니다 .




  0%|          | 0/875 [00:00<?, ?it/s]

*** Question : 지루하다, 놀러가고 싶어.
*** Predicted Answer : 연인 은 항상 좋 죠 .


*** Question : 오늘 일찍 일어났더니 피곤하다.
*** Predicted Answer : 그것 은 최선 의 선택 일거 라고 생각 해요 .


*** Question : 간만에 여자친구랑 데이트 하기로 했어.
*** Predicted Answer : 편안 하 게 말로 해 주 ㅂ시오 .


*** Question : 집에 있는다는 소리야.
*** Predicted Answer : 혼자 만 자 면 저 에게 매력 있 어요 .




  0%|          | 0/875 [00:00<?, ?it/s]

*** Question : 지루하다, 놀러가고 싶어.
*** Predicted Answer : 같이 살 기 직전 까지 이랑 같 죠 .


*** Question : 오늘 일찍 일어났더니 피곤하다.
*** Predicted Answer : 그것 이 최선 이 헛헛 하 답니다 .


*** Question : 간만에 여자친구랑 데이트 하기로 했어.
*** Predicted Answer : 그리워하 말 을 정확도 말로 은 의미 를 애틋 시키 게 하 는 편 이 좋 아요 .


*** Question : 집에 있는다는 소리야.
*** Predicted Answer : 자 면 좀 사 겨 보 세요 .




#### 시도 2

In [138]:

# Hyperparameters
print(f"Hyperparameters \n \
      n_layers={n_layers} \n \
      d_model={d_model} \n \
      n_heads={n_heads} \n \
      d_ff={d_ff} \n \
      src_vocab_size={src_vocab_size} \n \
      tgt_vocab_size={tgt_vocab_size} \n \
      pos_len = {pos_len} \n \
      dropout={dropout}")

print(f"Training Parameters \n \
      Warmup Steps={4000} \n \
      BATCH_SIZE={BATCH_SIZE}")


EPOCHS = 10

for epoch in range(EPOCHS):
    total_loss = 0
    
    dataset_count = tf.data.experimental.cardinality(train_dataset).numpy()
    tqdm_bar = tqdm(total=dataset_count)
    for step, (enc_batch, dec_batch) in enumerate(train_dataset):
        batch_loss, enc_attns, dec_attns, dec_enc_attns = \
        train_step(enc_batch,
                    dec_batch,
                    transformer,
                    optimizer)

        total_loss += batch_loss
        
        a = tqdm_bar.set_description_str('Epoch %2d' % (epoch + 1))
        a = tqdm_bar.set_postfix_str('Loss %.4f' % (total_loss.numpy() / (step + 1)))
        a = tqdm_bar.update()
        
    for question in questions:
        translate_eval(question, transformer, tokenizer, tokenizer)
        
    
#    eval_bleu(transformer, questions, answers, tokenizer, tokenizer, verbose=True)

Hyperparameters 
       n_layers=2 
       d_model=128 
       n_heads=4 
       d_ff=512 
       src_vocab_size=8325 
       tgt_vocab_size=8325 
       pos_len = 41 
       dropout=0.4
Training Parameters 
       Warmup Steps=4000 
       BATCH_SIZE=32


  0%|          | 0/875 [00:00<?, ?it/s]

*** Question : 지루하다, 놀러가고 싶어.
*** Predicted Answer : 짝사랑 을 것 같 아요 .


*** Question : 오늘 일찍 일어났더니 피곤하다.
*** Predicted Answer : 짝사랑 은 사랑 이 네요 .


*** Question : 간만에 여자친구랑 데이트 하기로 했어.
*** Predicted Answer : 짝사랑 은 사랑 을 수 있 어요 .


*** Question : 집에 있는다는 소리야.
*** Predicted Answer : 사랑 의 사랑 이 네요 .




  0%|          | 0/875 [00:00<?, ?it/s]

*** Question : 지루하다, 놀러가고 싶어.
*** Predicted Answer : 좋 은 사람 들 을 찾아보 세요 .


*** Question : 오늘 일찍 일어났더니 피곤하다.
*** Predicted Answer : 많이 되 지 않 은 사람 들 을 더 더 좋 아요 .


*** Question : 간만에 여자친구랑 데이트 하기로 했어.
*** Predicted Answer : 좋 은 사람 들 을 찾아보 세요 .


*** Question : 집에 있는다는 소리야.
*** Predicted Answer : 저 는 사람 들 을 찾아보 세요 .




...

*** Question : 지루하다, 놀러가고 싶어.
*** Predicted Answer : 그 사람 과 함께 있 는 사람 과 함께 있 을 거 예요 .


*** Question : 오늘 일찍 일어났더니 피곤하다.
*** Predicted Answer : 그것 지만 그것 이 집안일 을 줄 거 예요 .


*** Question : 간만에 여자친구랑 데이트 하기로 했어.
*** Predicted Answer : 연인 로 향수 놀드 라면 괜찮 죠 .


*** Question : 집에 있는다는 소리야.
*** Predicted Answer : 그게 상관없 지만 자기 의 취향 월과 거 예요 .




  0%|          | 0/875 [00:00<?, ?it/s]

*** Question : 지루하다, 놀러가고 싶어.
*** Predicted Answer : 같이 살 자고 프로 왕자


*** Question : 오늘 일찍 일어났더니 피곤하다.
*** Predicted Answer : 좀 더 알아볼 시간 이 중요 시키 꼼짝 않 는 게 좋 겠 네요 .


*** Question : 간만에 여자친구랑 데이트 하기로 했어.
*** Predicted Answer : 좋 은 소문 은 네요 .


*** Question : 집에 있는다는 소리야.
*** Predicted Answer : 참 상관없 군요 .




  0%|          | 0/875 [00:00<?, ?it/s]

*** Question : 지루하다, 놀러가고 싶어.
*** Predicted Answer : 다른 사람 들 과 같이 협조 해 보 는 어떨까 요 .


*** Question : 오늘 일찍 일어났더니 피곤하다.
*** Predicted Answer : 좀 더 알아볼 시간 그러 에요 .


*** Question : 간만에 여자친구랑 데이트 하기로 했어.
*** Predicted Answer : 될 거 예요 으며


*** Question : 집에 있는다는 소리야.
*** Predicted Answer : 그게 제일 괜찮 죠 .




In [158]:
# Hyperparameters
print(f"Hyperparameters \n \
      n_layers={n_layers} \n \
      d_model={d_model} \n \
      n_heads={n_heads} \n \
      d_ff={d_ff} \n \
      src_vocab_size={src_vocab_size} \n \
      tgt_vocab_size={tgt_vocab_size} \n \
      pos_len = {pos_len} \n \
      dropout={dropout}")

print(f"Training Parameters \n \
      Warmup Steps={4000} \n \
      BATCH_SIZE={BATCH_SIZE}")


EPOCHS = 10

for epoch in range(EPOCHS):
    total_loss = 0
    
    dataset_count = tf.data.experimental.cardinality(train_dataset).numpy()
    tqdm_bar = tqdm(total=dataset_count)
    for step, (enc_batch, dec_batch) in enumerate(train_dataset):
        batch_loss, enc_attns, dec_attns, dec_enc_attns = \
        train_step(enc_batch,
                    dec_batch,
                    transformer,
                    optimizer)

        total_loss += batch_loss
        
        a = tqdm_bar.set_description_str('Epoch %2d' % (epoch + 1))
        a = tqdm_bar.set_postfix_str('Loss %.4f' % (total_loss.numpy() / (step + 1)))
        a = tqdm_bar.update()
        
    for question in questions:
        translate_eval(question, transformer, tokenizer, tokenizer)
        
    
#    eval_bleu(transformer, questions, answers, tokenizer, tokenizer, verbose=True)

Hyperparameters 
       n_layers=2 
       d_model=64 
       n_heads=4 
       d_ff=512 
       src_vocab_size=8325 
       tgt_vocab_size=8325 
       pos_len = 41 
       dropout=0.3
Training Parameters 
       Warmup Steps=4000 
       BATCH_SIZE=32


  0%|          | 0/875 [00:00<?, ?it/s]

*** Question : 지루하다, 놀러가고 싶어.
*** Predicted Answer : 사랑 이 있 는 게 좋 겠 어요 .


*** Question : 오늘 일찍 일어났더니 피곤하다.
*** Predicted Answer : 사랑 은 사랑 이 있 아요 .


*** Question : 간만에 여자친구랑 데이트 하기로 했어.
*** Predicted Answer : 사랑 은 사랑 이 있 아요 .


*** Question : 집에 있는다는 소리야.
*** Predicted Answer : 사랑 은 사랑 이 있 아요 .




  0%|          | 0/875 [00:00<?, ?it/s]

*** Question : 지루하다, 놀러가고 싶어.
*** Predicted Answer : 짝사랑 이 있 을 수 도 있 을 거 예요 .


*** Question : 오늘 일찍 일어났더니 피곤하다.
*** Predicted Answer : 짝사랑 이 되 는 것 같 아요 .


*** Question : 간만에 여자친구랑 데이트 하기로 했어.
*** Predicted Answer : 짝사랑 의 사랑 이 에요 .


*** Question : 집에 있는다는 소리야.
*** Predicted Answer : 짝사랑 이 있 을 수 도 있 을 거 예요 .




...

*** Question : 지루하다, 놀러가고 싶어.
*** Predicted Answer : 공부 도와 달이 라고 해 보 세요 .


*** Question : 오늘 일찍 일어났더니 피곤하다.
*** Predicted Answer : 자연환경 스러운 현상 입니다 .


*** Question : 간만에 여자친구랑 데이트 하기로 했어.
*** Predicted Answer : 애틋 한 사랑 그러 네요 .


*** Question : 집에 있는다는 소리야.
*** Predicted Answer : 서로 에게 좋 은 월과 이 네요 .




  0%|          | 0/875 [00:00<?, ?it/s]

*** Question : 지루하다, 놀러가고 싶어.
*** Predicted Answer : 공부 도와 주기도 세요 .


*** Question : 오늘 일찍 일어났더니 피곤하다.
*** Predicted Answer : 시간 이 남 았 으면 좋 네요 .


*** Question : 간만에 여자친구랑 데이트 하기로 했어.
*** Predicted Answer : 경축 드려요 는데


*** Question : 집에 있는다는 소리야.
*** Predicted Answer : 축하 해요 캐치




  0%|          | 0/875 [00:00<?, ?it/s]

*** Question : 지루하다, 놀러가고 싶어.
*** Predicted Answer : 공부 도와 주기도 세요 .


*** Question : 오늘 일찍 일어났더니 피곤하다.
*** Predicted Answer : 시간 이 남 을까 ㄴ다는 게 좋 습니다 .


*** Question : 간만에 여자친구랑 데이트 하기로 했어.
*** Predicted Answer : 트라우마 ㄴ다는 이야기 군요 .


*** Question : 집에 있는다는 소리야.
*** Predicted Answer : 너무 잘 지내 고 있 어요 .




## Step 7. 성능 측정하기

### BLEU 평가

* 챗봇의 경우. 올바른 대답을 하는지가 중요한 평가 지표
* 성능 평가
  * 주어진 질문에 적절한 답변을 하는지 확인
  * BLUE Score  
    BLEU Score를 계산하는 calculate_bleu() 함수 적용

In [83]:
def calculate_bleu(reference, candidate, weights=[0.25, 0.25, 0.25, 0.25]):
    return sentence_bleu([reference],
                         candidate,
                         weights=weights,
                         smoothing_function=SmoothingFunction().method1)  # smoothing_function 적용

In [84]:
# 아래 두 문장을 바꿔가며 테스트 해보세요
reference = "많 은 자연어 처리 연구자 들 이 트랜스포머 를 선호 한다".split()
candidate = "적 은 자연어 학 개발자 들 가 트랜스포머 을 선호 한다 요".split()

reference
candidate

print("BLEU-1:", calculate_bleu(reference, candidate, weights=[1, 0, 0, 0]))
print("BLEU-2:", calculate_bleu(reference, candidate, weights=[0, 1, 0, 0]))
print("BLEU-3:", calculate_bleu(reference, candidate, weights=[0, 0, 1, 0]))
print("BLEU-4:", calculate_bleu(reference, candidate, weights=[0, 0, 0, 1]))

print("\nBLEU-Total:", calculate_bleu(reference, candidate))

['많', '은', '자연어', '처리', '연구자', '들', '이', '트랜스포머', '를', '선호', '한다']

['적', '은', '자연어', '학', '개발자', '들', '가', '트랜스포머', '을', '선호', '한다', '요']

BLEU-1: 0.5
BLEU-2: 0.18181818181818182
BLEU-3: 0.010000000000000004
BLEU-4: 0.011111111111111112

BLEU-Total: 0.05637560315259291


In [85]:
#MAX_LEN = pos_len = 41
def translate(tokens, model, src_tokenizer, tgt_tokenizer):
    padded_tokens = tf.keras.preprocessing.sequence.pad_sequences(tokens,
                                                           maxlen=MAX_LEN,
                                                           padding='post')
    ids = []
    #output = tf.expand_dims([tgt_tokenizer.bos_id()], 0)
    output = tf.expand_dims([tgt_tokenizer.word_index['<start>']], 0)
    for i in range(MAX_LEN):
        enc_padding_mask, combined_mask, dec_padding_mask = \
        generate_masks(padded_tokens, output)

        predictions, _, _, _ = model(padded_tokens, 
                                      output,
                                      enc_padding_mask,
                                      combined_mask,
                                      dec_padding_mask)

        predicted_id = \
        tf.argmax(tf.math.softmax(predictions, axis=-1)[0, -1]).numpy().item()

        #if tgt_tokenizer.eos_id() == predicted_id:
        if tgt_tokenizer.word_index['<end>'] == predicted_id:
            #result = tgt_tokenizer.decode_ids(ids)
            result = tgt_tokenizer.sequences_to_texts([ids])
            #print("1. result:", result)
            return result

        ids.append(predicted_id)
        output = tf.concat([output, tf.expand_dims([predicted_id], 0)], axis=-1)

    #result = tgt_tokenizer.decode_ids(ids)  
    result = tgt_tokenizer.sequences_to_texts([ids])
    #print("2. result:", result)
    return result


In [86]:
def eval_bleu_single(model, src_sentence, tgt_sentence, src_tokenizer, tgt_tokenizer, verbose=True):

    #src_tokens = src_tokenizer.encode_as_ids(src_sentence)
    #tgt_tokens = tgt_tokenizer.encode_as_ids(tgt_sentence)
   
    src_sentence = preprocess_sentence(src_sentence)  
    tgt_sentence = preprocess_sentence(tgt_sentence)  
    
    tokenizer = Mecab()
    src_sentence = tokenizer.morphs(src_sentence)
    tgt_sentence = tokenizer.morphs(tgt_sentence)
    src_tokens = src_tokenizer.texts_to_sequences([src_sentence])
    tgt_tokens = tgt_tokenizer.texts_to_sequences([tgt_sentence])
      
    #print(src_tokens)
    #print(tgt_tokens)
    #print(tgt_sentence)
 
    if (len(src_tokens[0]) > MAX_LEN): return None
    if (len(tgt_tokens[0]) > MAX_LEN): return None

    #reference = tgt_sentence.split()
    #candidate = translate(src_tokens, model, src_tokenizer, tgt_tokenizer).split()
    reference = tgt_sentence
    #candidate = " ".join(translate(src_tokens, model, src_tokenizer, tgt_tokenizer)).split()
    candidate = translate(src_tokens, model, src_tokenizer, tgt_tokenizer)[0].split()
    #print(translate(src_tokens, model, src_tokenizer, tgt_tokenizer))
    #print("ref:", reference ," can: ",candidate)
    
    score = sentence_bleu([reference], candidate,
                          smoothing_function=SmoothingFunction().method1)

    if verbose:
        print("Question: ", src_sentence)
        print("Prediction Answer: ", candidate)
        print("Real Answer: ", reference)
        print("BLEU Score: %lf\n" % score)
        
    return score
        
print('슝=3')

슝=3


#### test

In [159]:
# 인덱스를 바꿔가며 테스트해 보세요
test_idx = 0
questions[test_idx]
answers[test_idx]

eval_bleu_single(transformer, 
                 questions[test_idx],
                 answers[test_idx], 
                 tokenizer, 
                 tokenizer)

'지루하다, 놀러가고 싶어.'

'잠깐 쉬 어도 돼요 .'

Question:  ['지루', '하', '다', '놀', '러', '가', '고', '싶', '어', '.']
Prediction Answer:  ['공부', '도와', '주기도', '세요', '.']
Real Answer:  ['잠깐', '쉬', '어도', '돼요', '.']
BLEU Score: 0.053728



0.05372849659117709

In [88]:
def eval_bleu(model, src_sentences, tgt_sentence, src_tokenizer, tgt_tokenizer, verbose=True):
    total_score = 0.0
    sample_size = len(src_sentences)
    
    for idx in tqdm(range(sample_size)):
        score = eval_bleu_single(model, src_sentences[idx], tgt_sentence[idx], src_tokenizer, tgt_tokenizer, verbose)
        if not score: continue
        
        total_score += score
    
    print("Num of Sample:", sample_size)
    print("Total Score:", total_score / sample_size)
    
print("슝=3")

슝=3


In [160]:
# test
eval_bleu(transformer, questions, answers, tokenizer, tokenizer, verbose=True)

  0%|          | 0/4 [00:00<?, ?it/s]

Question:  ['지루', '하', '다', '놀', '러', '가', '고', '싶', '어', '.']
Prediction Answer:  ['공부', '도와', '주기도', '세요', '.']
Real Answer:  ['잠깐', '쉬', '어도', '돼요', '.']
BLEU Score: 0.053728

Question:  ['오늘', '일찍', '일어났', '더니', '피곤', '하', '다', '.']
Prediction Answer:  ['시간', '이', '남', '을까', 'ㄴ다는', '게', '좋', '습니다', '.']
Real Answer:  ['맛난', '거', '드세요', '.']
BLEU Score: 0.023980

Question:  ['간만에', '여자', '친구', '랑', '데이트', '하', '기', '로', '했', '어', '.']
Prediction Answer:  ['트라우마', 'ㄴ다는', '이야기', '군요', '.']
Real Answer:  ['떨리', '겠', '죠', '.']
BLEU Score: 0.053728

Question:  ['집', '에', '있', '는다는', '소리', '야', '.']
Prediction Answer:  ['너무', '잘', '지내', '고', '있', '어요', '.']
Real Answer:  ['좋', '아', '하', '면', '그럴', '수', '있', '어요', '.']
BLEU Score: 0.122852

Num of Sample: 4
Total Score: 0.06357243721516447


#### 시도 1

In [105]:
# Hyperparameters
print(f"Hyperparameters \n \
      n_layers={n_layers} \n \
      d_model={d_model} \n \
      n_heads={n_heads} \n \
      d_ff={d_ff} \n \
      src_vocab_size={src_vocab_size} \n \
      tgt_vocab_size={tgt_vocab_size} \n \
      pos_len = {pos_len} \n \
      dropout={dropout}")

print(f"Training Parameters \n \
      Warmup Steps={4000} \n \
      BATCH_SIZE={BATCH_SIZE}")


EPOCHS = 10

for epoch in range(EPOCHS):
    total_loss = 0
    
    dataset_count = tf.data.experimental.cardinality(train_dataset).numpy()
    tqdm_bar = tqdm(total=dataset_count)
    for step, (enc_batch, dec_batch) in enumerate(train_dataset):
        batch_loss, enc_attns, dec_attns, dec_enc_attns = \
        train_step(enc_batch,
                    dec_batch,
                    transformer,
                    optimizer)

        total_loss += batch_loss
        
        a = tqdm_bar.set_description_str('Epoch %2d' % (epoch + 1))
        a = tqdm_bar.set_postfix_str('Loss %.4f' % (total_loss.numpy() / (step + 1)))
        a = tqdm_bar.update()
        
    #for question in questions:
    #    translate_eval(question, transformer, tokenizer, tokenizer)
        
    
    eval_bleu(transformer, questions, answers, tokenizer, tokenizer, verbose=True)

Hyperparameters 
       n_layers=2 
       d_model=256 
       n_heads=4 
       d_ff=1048 
       src_vocab_size=8325 
       tgt_vocab_size=8325 
       pos_len = 41 
       dropout=0.4
Training Parameters 
       Warmup Steps=4000 
       BATCH_SIZE=32


  0%|          | 0/875 [00:00<?, ?it/s]

  0%|          | 0/4 [00:00<?, ?it/s]

Question:  ['지루', '하', '다', '놀', '러', '가', '고', '싶', '어', '.']
Prediction Answer:  ['짝사랑', '을', '수', '있', '을', '거', '예요', '.']
Real Answer:  ['잠깐', '쉬', '어도', '돼요', '.']
BLEU Score: 0.027776

Question:  ['오늘', '일찍', '일어났', '더니', '피곤', '하', '다', '.']
Prediction Answer:  ['짝사랑', '의', '사랑', '을', '수', '있', '을', '거', '예요', '.']
Real Answer:  ['맛난', '거', '드세요', '.']
BLEU Score: 0.025099

Question:  ['간만에', '여자', '친구', '랑', '데이트', '하', '기', '로', '했', '어', '.']
Prediction Answer:  ['짝사랑', '을', '수', '있', '을', '거', '예요', '.']
Real Answer:  ['떨리', '겠', '죠', '.']
BLEU Score: 0.027776

Question:  ['집', '에', '있', '는다는', '소리', '야', '.']
Prediction Answer:  ['짝사랑', '의', '사랑', '의', '사랑', '이', '에요', '.']
Real Answer:  ['좋', '아', '하', '면', '그럴', '수', '있', '어요', '.']
BLEU Score: 0.024512

Num of Sample: 4
Total Score: 0.02629085096624226


  0%|          | 0/875 [00:00<?, ?it/s]

...

  0%|          | 0/4 [00:00<?, ?it/s]

Question:  ['지루', '하', '다', '놀', '러', '가', '고', '싶', '어', '.']
Prediction Answer:  ['그러', '면', '좋', '은데', '사람', '만날', '수', '있', '어요', '.']
Real Answer:  ['잠깐', '쉬', '어도', '돼요', '.']
BLEU Score: 0.021105

Question:  ['오늘', '일찍', '일어났', '더니', '피곤', '하', '다', '.']
Prediction Answer:  ['다른', '사람', '은', '들', '이', '별로', '라고', '판단', '을', '들', '것', '예요', '.']
Real Answer:  ['맛난', '거', '드세요', '.']
BLEU Score: 0.015537

Question:  ['간만에', '여자', '친구', '랑', '데이트', '하', '기', '로', '했', '어', '.']
Prediction Answer:  ['공원', '이나', '호칭', '은', '깔끔', '할', '것', '예요', '.']
Real Answer:  ['떨리', '겠', '죠', '.']
BLEU Score: 0.023980

Question:  ['집', '에', '있', '는다는', '소리', '야', '.']
Prediction Answer:  ['좋', '지요', '는데']
Real Answer:  ['좋', '아', '하', '면', '그럴', '수', '있', '어요', '.']
BLEU Score: 0.015377

Num of Sample: 4
Total Score: 0.018999955016110116


  0%|          | 0/875 [00:00<?, ?it/s]

  0%|          | 0/4 [00:00<?, ?it/s]

Question:  ['지루', '하', '다', '놀', '러', '가', '고', '싶', '어', '.']
Prediction Answer:  ['같이', '살', '면서', '같이', '살', '면서', '놀', '아요', '.']
Real Answer:  ['잠깐', '쉬', '어도', '돼요', '.']
BLEU Score: 0.023980

Question:  ['오늘', '일찍', '일어났', '더니', '피곤', '하', '다', '.']
Prediction Answer:  ['짝사랑', '은', '행복', '그러', '에요', '.']
Real Answer:  ['맛난', '거', '드세요', '.']
BLEU Score: 0.040825

Question:  ['간만에', '여자', '친구', '랑', '데이트', '하', '기', '로', '했', '어', '.']
Prediction Answer:  ['건강', '은', '해서', '매달리', '겠', '어요', '.']
Real Answer:  ['떨리', '겠', '죠', '.']
BLEU Score: 0.039281

Question:  ['집', '에', '있', '는다는', '소리', '야', '.']
Prediction Answer:  ['좋', '아', '하', '는', '감정', '지요', '.']
Real Answer:  ['좋', '아', '하', '면', '그럴', '수', '있', '어요', '.']
BLEU Score: 0.132014

Num of Sample: 4
Total Score: 0.05902503732512437


## 회고